In [2]:
import pandas as pd
from datetime import datetime
from datetime import timedelta
from tqdm import tqdm, tqdm_notebook
import  numpy as np

Часть 1. Загрузка данных

In [3]:
db1 = pd.read_excel('recdata2016-2017.xlsx')

In [4]:
#включает данные за 2019 год

In [5]:
db2 = pd.read_excel('recdata2018.xlsx')

In [6]:
db = pd.concat([db1,db2], ignore_index=True)

In [7]:
db.columns

Index(['OrderID', 'OrderTotalPrice', 'OrderDate', 'OrderSiteID',
       'OrderCustomerID', 'OrderItemUnitCount', 'isbn', 'title', 'annotation',
       'title.1', 'authorid', 'pformat', 'cover', 'paper', 'color', 'pages',
       'size', 'nweight', 'age', 'CustomerCreated'],
      dtype='object')

In [8]:
db.dropna(inplace=True)

In [9]:
db.shape

(742253, 20)

In [10]:
def db_transform(db):
    
    #формат даты заказа
    db['OrderDate'] = [x for x in pd.to_datetime(db['OrderDate'])]
    #формат даты регистрации
    db['CustomerCreated'] = [x for x in pd.to_datetime(db['CustomerCreated'])]
    #для каждого записи- сколько времени прошло между датой заказа и датой регистрации
    db['day_after_reg'] = db['OrderDate'] - db['CustomerCreated']
    #то же самое в днях
    db['day_after_reg'] = [x.days for x in db['day_after_reg']]
    #делим жизнь покупателя на 9-месячные промежутки, 1- первые 9 мес с регистрации, 2-270-540 дней с начала регистрации и тд
    db['group']=[x//270 + 1 for x in db['day_after_reg']]
    db['theme']=db['title.1'].values.tolist()
    db['OrderCustomerID']=[str(x) for x in db['OrderCustomerID']]
    db['group']=[str(x) for x in db['group']]
    db['cus-ergroup']=db['OrderCustomerID'] + ' ' + db['group']
    return db

In [11]:
db = db_transform(db)

In [ ]:
#Трансформируем возраст в db по нужным нам группам

In [12]:
age_initial = db['age'].value_counts().index.tolist()

In [13]:
age_initial

[datetime.datetime(2019, 6, 4, 0, 0),
 '0-3',
 datetime.datetime(2019, 11, 7, 0, 0),
 datetime.datetime(2019, 6, 3, 0, 0),
 'Для взрослых',
 '12+',
 datetime.datetime(2019, 9, 5, 0, 0),
 '6+',
 '0+',
 '7+']

In [14]:
new_age_list = []
for i in db['age']:
    if i == '3+':
        new_age_list.append('4-6')
    elif i == '3-6':
        new_age_list.append('4-6')
    elif i == '0+':
        new_age_list.append('0-3')
    elif i == '2+':
        new_age_list.append('0-3')
    elif i == '6+':
        new_age_list.append('7-11')
    elif i == '5+':
        new_age_list.append('7-11')
    elif i == '7+':
        new_age_list.append('7-11')
    elif i == age_initial[0]:
        new_age_list.append('4-6')                   
    elif i == age_initial[2]:
        new_age_list.append('7-11')                        
    elif i == age_initial[3]:
        new_age_list.append('4-6')                             
    elif i == age_initial[6]:
        new_age_list.append('7-11')                                    
    elif i == '5-9':
        new_age_list.append('7-11')
    else:
        new_age_list.append(i)
db['age'] = new_age_list

In [15]:
#Трансформируем тему (делаем так, чтобы потом было удобно кодировать тему как текст (убираем пробелы))
db['theme'] = [x.replace(' ','') for x in db['theme']]
db['theme'] = [x.replace(',','') for x in db['theme']]
db['theme'] = [x.replace('-','') for x in db['theme']]
db['theme'] = [x.replace('(','') for x in db['theme']]
db['theme'] = [x.replace(')','') for x in db['theme']]
db['theme'] = [x.replace('+','') for x in db['theme']]

In [16]:
db['theme'].value_counts()

Познавательнаялитературадошкольники    329566
Художественнаялитературадлядетей       158725
Развлекательнаялитература              144594
Учебнаялитературашкольники              34077
Энциклопедиидлядетей                    26527
Игрыдосугирукоделие                     19669
Психологияивоспитаниедетей              14811
Познавательнаялитературашкольники        8679
Allagetrendbooksnonfiction               4616
Книгидлявзрослых                          989
Name: theme, dtype: int64

In [17]:
#Трансформируем теги

In [18]:
tab_book = db[['isbn','annotation']]

In [19]:
tab_book.drop_duplicates(inplace = True)

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [20]:
tab_book.head()

isbn                                         annotation
806   978-5-906824-43-1     Эта книга-раскраска дарит самое ценное в жизни...
869   978-5-906824-45-5     Эта книга-раскраска дарит самое ценное в жизни...
1043  978-5-906824-44-8     Эта книга-раскраска дарит самое ценное в жизни...
2136  978-5-91982-404-6     Этот роскошный альбом, проиллюстрированный вел...
2367  978-5-91982-145-8     Ален Пассар – знаменитый французский шеф-повар...

In [21]:
import re
regex = re.compile("[А-Яа-я]+")

def words_only(text, regex=regex):
    try:
        return " ".join(regex.findall(text))
    except:
        return ""

In [22]:
import nltk
nltk.download('stopwords')

from nltk.corpus import stopwords
noise = stopwords.words('russian')
noise = noise + ['это', 'тыс', 'млн', 'млрд', 'также']
mystoplemmas = ['который','прошлый','сей', 'свой', 'наш','ваш','реб' ,'нка','нку','нок','нком','вес','ещ','абсолютно',
                'абсолютный','мочь','этот','малыш','ребенок', 'автор','такой', ' ', '\n', 'лый','лому', 'лого', 'лым', 
                'лом', 'какой','веселый', 'весело', 'новый', 'разворот', 'страничка','подойда', 'нужный','каждый','позволить',
                'интересный','страница', 'важный', 'красочный', 'яркий', 'серия','коллекция','нный','эх','влюблять',
                'распространа','многий','традиционный','галан', 'таки','найда','давно','понравиться','вс','ой','чей',
                'ра','тно','гкость','очень','довольный','обожаемоия','различный','разный']

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\n.volkova\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [23]:
def dataprep(i, tab):
    
    dp = [words_only(x.lower()) for x in tab[i]]
    dp = [x.replace(' ',',').split(',') for x in dp]
    long_words = []
    for j in tqdm(dp):
        long_words.append([x for x in j if len(x)>1])
    latterm_wo_stopw = []
    for k in tqdm(long_words):
        latterm_wo_stopw.append(' '.join([x for x in k if x not in noise]))
    return latterm_wo_stopw

In [24]:
from rnnmorph.predictor import RNNMorphPredictor
predictor = RNNMorphPredictor(language = 'ru')

Using TensorFlow backend.
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\keras\engine\saving.py:473: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  config = yaml.load(yaml_string)


Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [25]:
def lem(a):
    
    res = []
    for i in tqdm(a):
        i = i.split(' ')
        forms = predictor.predict(i)
        res.append([word.normal_form for word in forms])
    return res

In [26]:
def lem_wo_stop(a):
    
    latterm = []
    for i in tqdm(a):
        latterm.append(' '.join([x for x in i if x not in mystoplemmas]))
    return latterm

In [27]:
annot_transform = dataprep('annotation', tab_book)

100%|███████████████████████████████████████████████████████████████████████████| 1337/1337 [00:00<00:00, 10714.74it/s]


In [28]:
annot_transform = lem(annot_transform)
annot_transform = lem_wo_stop(annot_transform)

100%|███████████████████████████████████████████████████████████████████████████| 1337/1337 [00:00<00:00, 27862.28it/s]


In [29]:
annot_transform[0]

'книга раскраска дарить самый ценный жизнь время принадлежать сам следовать замысел художник превращать наполненный цифра линия рисунок редкий прекрасный возможность остановитьсява вечный бег побыть наедине себя устать раздражённый жд тот нечего занять взять рука карандаш раскрашивать мир живой природа предстать вы многоцветие разнообразие творчество прекрасный способ снять напряжение освободить голова тревожный мысль негативный эмоция'

In [30]:
tab_book['annotation_transform'] = annot_transform

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [31]:
tab_book.drop('annotation', axis = 1, inplace = True)

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [32]:
db = db.merge(tab_book, how = 'left', on = 'isbn')

In [33]:
db['annotation'] = db['annotation_transform']

In [34]:
db.drop('annotation_transform', axis = 1, inplace = True)

In [35]:
#Формируем таблицу исходник для формирования X и y
def tab_creation(period):
    
    #вытаскиваем уникальные сочетания customer id и нужного периода (группа-9мес или следующий заказ) и формируем  таблицу
    #для тегов нам нужна только группировка по юзерам, поэтому если period=='OrderCustomerID', 
    #то делаем таблицу просто группировкой по юзерам
    if period == 'OrderCustomerID':
        tab = db.groupby(['OrderCustomerID']).max().reset_index()[['OrderCustomerID','day_after_reg']]
    else:
        tab = db.groupby(['OrderCustomerID',period]).max().reset_index()[['OrderCustomerID',period,'day_after_reg']]
        #приводим customer id к текстовому формату
        tab['OrderCustomerID'] = [str(x) for x in tab['OrderCustomerID']]
        #приводим период  к текстовому формату
        tab[period] = [str(x) for x in tab[period]]
        #соединяем customer id и период
        tab['cus-ergroup'] = tab['OrderCustomerID'] + ' ' + tab[period]
    return tab

In [36]:
#таблица для предсказания изменения фактора в следующем периоде (возраст/тема) и предсказанию покупки по тегам. 
#На основании распределения возраста предыдущем жизненном периоде предсказываем возраст в следующем
#На основании распределения тем в предыдущем жизненном периоде предсказываем, какую тему предпочтет юзер в следующем
#На основании распределения тегов в предыдущем жизненном периоде предсказываем вероятность покупки в следующем
tab_factor = tab_creation('group')

In [37]:
tab_factor.head()

OrderCustomerID group  day_after_reg cus-ergroup
0          100131     1             72    100131 1
1          101311     1             35    101311 1
2          102222     1            163    102222 1
3          103241     1              0    103241 1
4          103537     1              0    103537 1

In [38]:
#для обучения с учителем нам нужно выбрать юзеров, которые жили более одного периода
def tab_more_1period_transform(tab):
    
    #Считаем количество повторений юзера в таблице- это и будет количеством периодов 
    tab_users = pd.DataFrame(tab['OrderCustomerID'].value_counts())
    #Выбираем юзеров, у которых периодов больше 1.
    tab_users = tab_users[tab_users['OrderCustomerID']>1]
    tab_users = tab_users.index.tolist()
    #Удаляем юзеров, у которых менее 1 периода
    customer_num = tab['OrderCustomerID'].values
    for line in tqdm(range(len(tab))):
        if customer_num[line] not in tab_users:
            tab.drop(line, axis = 0, inplace = True)
    return tab

In [39]:
tab_factor = tab_more_1period_transform(tab_factor)

100%|███████████████████████████████████████████████████████████████████████████| 87028/87028 [08:50<00:00, 164.09it/s]


In [ ]:
#Подготавливаем исходники для X и y. 
#X будет содержать информацию о пользователе (по факторам), о конкретной книге, 
#y -факт покупки книги с соответствующим фактором

In [ ]:
#Исходник для X - данные по покупках книг пользователями за последние 9 месяцев их Lifecycle

In [ ]:
#1 этап подготовки исходника для X- готовим данные о книгах, которые были куплены пользователями за последние 9 мес

In [40]:
def tab_forX_books():
    
    #Готовим список юзеров, содержащихся в таблице для тем
    tab_users2 = pd.DataFrame(tab_factor['OrderCustomerID'].value_counts())
    tab_users2 = tab_users2.index.tolist()
    #Готовим исходник для таблицы, содержащий id клиента,группу-период и id+группа
    res_cus = [] #список клиентов
    res_gr = []  #список групп
    res_cgr = [] #список групп+клиентов 
    #выделяем последний по времени для каждого юзера группу-период
    for i in tqdm(tab_users2):
        res_cus.append(i)
        z = str(max([int(x) for x in tab_factor[tab_factor['OrderCustomerID'] == i]['group'].values]))
        res_gr.append(z)
        res_cgr.append(i + ' ' + z)
    #Образуем таблицы для юзеров, групп, юзер+группа
    tab_cus = pd.DataFrame(res_cus, columns = ['OrderCustomerID'])
    tab_gr = pd.DataFrame(res_gr, columns = ['group'])
    tab_cgr = pd.DataFrame(res_cgr, columns = ['cus-ergroup'])
    #Объединяем в 1 таблицу и присваеваем имена колонкам
    tab_y = pd.concat([tab_cus, tab_gr, tab_cgr], axis = 1,ignore_index = True)
    tab_y.columns = ['OrderCustomerID', 'group', 'cus-ergroup']
    # Выделяем из db строки, соответсвующие строкам в tab_y, корректируем имена колонок, перезаписываем tab_y
    db_forY = db.copy()
    db_forY.reset_index(inplace = True)
    db_forY.drop('index', axis = 1,inplace=True)
    db_forY = db_forY.merge(tab_y, how = 'left', on = 'cus-ergroup')
    db_forY.dropna(inplace=True)
    db_forY.drop(['OrderCustomerID_y','group_y'], axis = 1, inplace = True)
    db_forY['OrderCustomerID'] = db_forY['OrderCustomerID_x']
    db_forY['group'] = db_forY['group_x']
    db_forY.drop(['OrderCustomerID_x','group_x'], axis = 1, inplace = True)
    tab_y = db_forY.copy()
    return tab_y

In [41]:
#Создаем таблицу, содержащию информацию о книгах, покупки которых нужно предсказать.
#Это позитивные примеры
tab_forX_books = tab_forX_books()

100%|█████████████████████████████████████████████████████████████████████████████| 7835/7835 [00:15<00:00, 507.63it/s]


In [42]:
tab_forX_books.shape

(81573, 24)

In [43]:
one = len(tab_forX_books)

In [44]:
#Делаем список книг для формирования отрицательных примеров

In [45]:
books = db.groupby(['isbn', 'age', 'theme']).sum().sort_values(by = ['OrderItemUnitCount'], ascending = False)
books.reset_index(inplace = True)

In [46]:
books['OrderItemUnitCount'].describe()

count    1337.000000
mean      665.799551
std       782.654036
min         1.000000
25%       125.000000
50%       386.000000
75%       918.000000
max      5911.000000
Name: OrderItemUnitCount, dtype: float64

In [47]:
sales_rating = []
for i in books['OrderItemUnitCount']:
    if i > 3000:
        sales_rating.append(1)
    elif i > 1000:
        sales_rating.append(2)
    elif i > 700:
        sales_rating.append(3)
    elif i > 300:
        sales_rating.append(4)
    else:
        sales_rating.append(5)
books['sales_rating'] = sales_rating

In [48]:
books=books.sort_values(by = ['age', 'OrderItemUnitCount'], ascending = False)

In [49]:
books.reset_index(inplace = True)

In [50]:
age_list = [1]
for i in range(1,len(books['age'])):
    if books['age'][i] == books['age'][i-1]:
        age_list.append(age_list[i-1]+1)
    else:
        age_list.append(1)

In [51]:
books['age_rating'] = age_list

In [52]:
books = books.sort_values(by = ['theme', 'OrderItemUnitCount'], ascending = False)

In [53]:
books.reset_index(inplace = True)

In [54]:
theme_list = [1]
for i in range(1,len(books['theme'])):
    if books['theme'][i] == books['theme'][i-1]:
        theme_list.append(theme_list[i-1]+1)
    else:
        theme_list.append(1)
books['theme_rating'] = theme_list

In [55]:
books=books.sort_values(by = ['sales_rating','age_rating', 'theme_rating'])['isbn'].values.tolist()

In [56]:
#Добавляем отрицательные примеры
import random
customers_positive_lines = tab_forX_books['OrderCustomerID'].values.tolist()

#создаем таблицу для негативных примеров с фактами покупок конкретных книг
FORneg_X = db[['isbn', 'title', 'OrderCustomerID']]
#делаем сводную, чтобы выделить книги, которые не покупались пользователем
FORneg_X = pd.pivot_table(FORneg_X, 
                        columns = ['isbn'], 
                        index = ['OrderCustomerID'], 
                        aggfunc = lambda x:len(x.unique()))
FORneg_X.columns = FORneg_X.columns.droplevel()
FORneg_X.fillna(0, inplace = True)

#делаем список книг, которые не покупались для каждого пользователя
customers = tab_forX_books.groupby('OrderCustomerID').count().index.tolist()
X_neg_books = {}
for i in tqdm(customers):
    x_n = []
    for j in tqdm(books):
        if FORneg_X[j][i] == 0:
            x_n.append(j)
    X_neg_books[i] = x_n
tab_forX_books_T = tab_forX_books.T
tab_forX_books_T.columns = tab_forX_books['isbn'].values.tolist()
columns=['isbn','title','annotation', 'title.1','authorid', 'pformat','cover','paper','color','pages',
         'size','nweight','age','theme']

#добавляем отрицательные примеры в таблицу к позитивным
for i in tqdm(range(len(customers_positive_lines))):
    j = X_neg_books[customers_positive_lines[i]][0]
    neg_tab = tab_forX_books.iloc[i:(i+1)].copy()
    try:
        for k in columns:
            neg_tab[k] = tab_forX_books_T[j].iloc[:,1][k] 
    except:
        continue
    X_neg_books[customers_positive_lines[i]].remove(X_neg_books[customers_positive_lines[i]][0])
    tab_forX_books = pd.concat([tab_forX_books, neg_tab], axis=0)

  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


...

  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


100%|██████████████████████████████████████████████████████████████████████████| 81573/81573 [2:55:07<00:00,  5.45it/s]


In [57]:
tab_forX_books.shape

(148644, 24)

In [58]:
tab_forX_books.to_excel('tab_forX_books.xlsx')

In [59]:
tab_forX_books['buyornot'] = list(np.ones(one)) + list(np.zeros(tab_forX_books.shape[0] - one))

In [60]:
#2 этап подготовки исходника для X- фомируем данные о пользователю по соответсвующему фактору
#за время с даты регистрации до покупки книг из tab_forX_books
#Убираем из tab  данные, содержащиеся в tab_forX_books, 
#чтобы в историю покупателя не была занесена информация о будущих покупках

In [61]:
#Функция по созданию таблицы с информацией о пользователе по различным факторам
#(история его покупок книг с определенным свойством- возраст, тема, тег)
def tabprep(tab, factor, period):
    
    tab.reset_index(inplace = True)
    tab.drop('index', axis = 1, inplace = True)
    #выделяем данные, содержащиеся в tab_forX_books
    user_next_period = tab_forX_books['cus-ergroup'].values.tolist()
    #убираем эти данные из db
    db_forX_user = db[db['cus-ergroup'].isin(user_next_period) == False]
    col = []
    #формируем вектор пользователя по фактору
    for j in tqdm(tab[period]):
        tab1 = db_forX_user[db_forX_user[period] == j]
        res = ' '.join(tab1[factor].values.tolist()) 
        col.append(res)
    tab3 = tab.copy()
    tab3[factor] = col
    tab2 = tab3[['OrderCustomerID','group','cus-ergroup','day_after_reg', factor]]
    return tab2

In [62]:
#Далее перейдем к построению baseline и разработке модели для создания рекомендаций

In [63]:
#Прежде всего разработаем фукнкцию для оценки рекомендаций- precision at k

In [64]:
check_prec_k = db[['isbn', 'OrderCustomerID']]
def mean_av_precision_at_k(dict_prediction, k):
    
    user_precision_list = []
    for i in tqdm(customers):
        try:
            cus_book_list = check_prec_k[check_prec_k['OrderCustomerID'] == i]['isbn'].values.tolist()
            #Книги изначально были отсортированы в порядке предпочтительности
            user_pred = dict_prediction[i][:k]
            user_precision = [1 if z in cus_book_list else 0 for z in user_pred]
            user_precision_transform = []
            for j in user_precision:
                if j > 0:
                    a = j + sum(user_precision_transform)
                else:
                    a = 0
                user_precision_transform.append(a)
            av_precision_k = sum([x/(user_precision_transform.index(x) + 1) for x in user_precision_transform])/k
            user_precision_list.append(av_precision_k)
        except:
            continue
    return np.mean(user_precision_list), user_precision_list

In [65]:
#Baseline- топ продаж по темам и возрастам

In [66]:
for_exclude = tab_forX_books['cus-ergroup'].values.tolist()

In [67]:
top_db = db[db['cus-ergroup'].isin(for_exclude) == False]

In [68]:
FORtop = top_db[['isbn', 'title', 'OrderCustomerID']]

#делаем сводную, чтобы выделить книги, которые не покупались пользователем
FORtop = pd.pivot_table(FORtop, columns = ['isbn'], index = ['OrderCustomerID'], aggfunc = lambda x:len(x.unique()))
FORtop.columns = FORtop.columns.droplevel()
FORtop.fillna(0, inplace = True)

#делаем список книг, которые не покупались для каждого пользователя
X_top_books = {}
for i in tqdm(customers):
    x_top = []
    for j in tqdm(books):
        if FORtop[j][i] == 0:
            x_top.append(j)
    X_top_books[i] = x_top

  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


...

  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


  0%|                                                                                         | 0/1337 [00:00<?, ?it/s]


100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [02:12<00:00, 59.07it/s]


In [69]:
metric = mean_av_precision_at_k(X_top_books, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:09<00:00, 25.32it/s]


In [70]:
metric[0]

0.011682514358647096

In [ ]:
#Mean average precision at k для топ-продаж составляет 1,2%

Возраст

In [71]:
#Делаем прогноз по возрасту

In [72]:
tab_age_usersForX = tabprep(tab_factor, 'age', 'cus-ergroup')

100%|████████████████████████████████████████████████████████████████████████████| 16895/16895 [09:47<00:00, 28.88it/s]


In [73]:
tab_age_usersForX['age'] = [np.nan if x == '' else x for x in tab_age_usersForX['age']]

In [74]:
tab_age_usersForX.dropna(inplace = True)

In [75]:
tab_age_usersForX.head()

OrderCustomerID group cus-ergroup  day_after_reg  \
0           32185     1     32185 1              0   
2           32186     1     32186 1             57   
4           32188     1     32188 1              0   
5           32188     2     32188 2            520   
7           32190     1     32190 1              0   

                                                 age  
0                                            4-6 4-6  
2                    0-3 0-3 0-3 0-3 0-3 4-6 0-3 0-3  
4  7-11 7-11 7-11 4-6 4-6 4-6 7-11 7-11 7-11 4-6 4-6  
5                                   4-6 4-6 4-6 7-11  
7                                            0-3 0-3

In [76]:
#Выделяем последний период для каждого покупателя и создаем список покупатель+последний период
cus_inTab_age = tab_age_usersForX.groupby('OrderCustomerID').count().index.tolist()
sp_maxgr = []
for i in cus_inTab_age:
    tab_Formax = tab_age_usersForX[tab_age_usersForX['OrderCustomerID'] == i]
    max_group = max(tab_Formax['group'].values)
    sp_maxgr.append(i + ' ' + max_group)

In [77]:
#Отбираем данные по последнему периоду для каждого пользователя
tab_age_usersForX = tab_age_usersForX[tab_age_usersForX['cus-ergroup'].isin(sp_maxgr)]

In [78]:
#Формируем таблицу, содержащую информацию по распределению покупок по возрастам в прошлом
#Возраст в последнем периоде (то, что нужно предсказать)
#Сколько прошло в днях между последним и предпоследним периодом
age_predict = tab_forX_books[['OrderCustomerID', 'age','day_after_reg']].merge(tab_age_usersForX, 
                                                                             on = 'OrderCustomerID', 
                                                                             how = 'left')

In [79]:
age_predict['day_after_reg'] = age_predict['day_after_reg_x'] - age_predict['day_after_reg_y']

In [80]:
age_y = age_predict['age_x'].values

In [81]:
#кодируем возраст
from sklearn.preprocessing import LabelEncoder
LabelEncoder = LabelEncoder()
age_y = LabelEncoder.fit_transform(age_y)

In [82]:
age_X = age_predict[['age_y','day_after_reg']]

In [83]:
age_X['age_y'] = [x.split() for x in age_X['age_y']]
new_ages = []
for  i in age_X['age_y']:
    res = [x.replace('-','') for x in i]
    res = [x.replace(' ','') for x in res]
    res = [x.replace('+','') for x in res]
    new_ages.append(' '.join(res))
age_X['age_y'] = new_ages

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [84]:
age_X['age_y'] = [x.replace('Для взрослых', 'длявзрослых') for x in age_X['age_y']]

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [85]:
#Считаем количество каждого возраста в прошлом

In [86]:
from sklearn.feature_extraction.text import CountVectorizer

In [87]:
vectorizer_c = CountVectorizer()

In [88]:
count_age = vectorizer_c.fit_transform(age_X['age_y'])

In [89]:
age_X = pd.concat([pd.DataFrame(count_age.toarray(), columns = vectorizer_c.get_feature_names()), 
                 pd.DataFrame(age_X['day_after_reg'])],
                 axis = 1, ignore_index = True)

In [90]:
from sklearn.model_selection import train_test_split
X_train_age, X_test_age, y_train_age, y_test_age = train_test_split(age_X, age_y, 
                                                                    test_size = 0.6, 
                                                                    random_state = 42)

In [91]:
X_train_age_for_ac, X_test_age_for_ac, y_train_age_for_ac, y_test_age_for_ac = train_test_split(age_X[:one], 
                                                                                                age_y[:one], 
                                                                                                test_size = 0.4, 
                                                                                                random_state = 42)

In [92]:
from sklearn.ensemble import RandomForestClassifier
r_forest=RandomForestClassifier(n_estimators = 100, max_depth = 12,random_state = 0)
r_forest.fit(X_train_age_for_ac, y_train_age_for_ac)  

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=12, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=None,
            oob_score=False, random_state=0, verbose=0, warm_start=False)

In [93]:
from sklearn.metrics import *

In [94]:
age_pred = r_forest.predict_proba(X_test_age_for_ac)

In [95]:
age_pred_factor = r_forest.predict_proba(X_test_age)

In [96]:
accuracy_score([np.argmax(x) for x in age_pred], y_test_age_for_ac)

0.5444682807232608

In [ ]:
#Accuracy Random forest для возраста составляет 54%

In [97]:
import xgboost as xgb
data = X_train_age_for_ac
label = y_train_age_for_ac
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
param['objective'] = 'multi:softprob'
param['num_class'] = 5
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data = X_test_age_for_ac
dtest = xgb.DMatrix(data)
age_pred = bst.predict(dtest)

In [98]:
accuracy_score([np.argmax(x) for x in age_pred], y_test_age_for_ac)

0.5696598222494637

In [ ]:
#Accuracy XGboost для возраста составляет 57%

In [ ]:
#Xgboost сработал лучше

In [309]:
LabelEncoder.inverse_transform([0,1,2,3,4])

array(['0-3', '12+', '4-6', '7-11', 'Для взрослых'], dtype=object)

In [99]:
data = X_test_age
dtest = xgb.DMatrix(data)
age_pred_factor = bst.predict(dtest)

In [ ]:
#Записываем фактор возраста

In [100]:
age_features = pd.DataFrame(age_pred_factor)

In [101]:
age_features.head()

0         1         2         3         4
0  0.092540  0.008441  0.718669  0.179379  0.000971
1  0.699544  0.000390  0.287842  0.008020  0.004204
2  0.527011  0.006333  0.436577  0.028525  0.001555
3  0.748151  0.002824  0.167841  0.079889  0.001295
4  0.178821  0.003241  0.629090  0.182932  0.005916

In [ ]:
#Прогнозируем тему

In [102]:
tab_theme_usersForX = tabprep(tab_factor, 'theme', 'OrderCustomerID')

100%|████████████████████████████████████████████████████████████████████████████| 16895/16895 [09:39<00:00, 29.13it/s]


In [103]:
tab_theme_usersForX = tab_theme_usersForX[['OrderCustomerID','theme']]

In [104]:
tab_theme_usersForX.drop_duplicates(inplace=True)

In [105]:
tab_theme_usersForX.head()
tab_theme_usersForX.reset_index(inplace=True)
tab_theme_usersForX.drop('index', axis=1, inplace=True)

In [106]:
tab_theme_usersForX.head()

OrderCustomerID                                              theme
0           32185  Учебнаялитературашкольники Учебнаялитературашк...
1           32186  Художественнаялитературадлядетей Познавательна...
2           32188  Художественнаялитературадлядетей Художественна...
3           32190  Художественнаялитературадлядетей Развлекательн...
4           32192                Познавательнаялитературадошкольники

In [107]:
#Считаем количество покупок по темам в прошлом

In [108]:
count_theme = vectorizer_c.fit_transform(tab_theme_usersForX['theme'])

In [109]:
count_theme.toarray()

array([[ 0,  0,  0, ...,  2,  0,  0],
       [ 0,  0,  0, ...,  0,  1,  0],
       [ 0,  0,  0, ...,  0,  8,  2],
       ...,
       [ 0,  0,  1, ...,  0,  0,  0],
       [ 0,  0,  0, ...,  4, 11,  1],
       [ 0,  0,  0, ...,  0,  0,  0]], dtype=int64)

In [110]:
tab_theme_usersForX = pd.concat([tab_theme_usersForX['OrderCustomerID'],
                               pd.DataFrame(count_theme.toarray())], 
                               axis = 1, 
                               ignore_index = True)

In [111]:
tab_theme_usersForX.columns = ['OrderCustomerID'] + vectorizer_c.get_feature_names()

In [112]:
tab_theme_usersForX.head()

OrderCustomerID  allagetrendbooksnonfiction  игрыдосугирукоделие  \
0           32185                           0                    0   
1           32186                           0                    0   
2           32188                           0                    0   
3           32190                           0                    0   
4           32192                           0                    0   

   книгидлявзрослых  познавательнаялитературадошкольники  \
0                 0                                    0   
1                 0                                    4   
2                 0                                    2   
3                 0                                    0   
4                 0                                    1   

   познавательнаялитературашкольники  психологияивоспитаниедетей  \
0                                  0                           0   
1                                  0                           0   
2                                  0                           0   
3                                  0                           0   
4                                  0                           0   

   развлекательнаялитература  учебнаялитературашкольники  \
0                          0                           2   
1                          3                           0   
2                          3                           0   
3                          1                           0   
4                          0                           0   

   художественнаялитературадлядетей  энциклопедиидлядетей  
0                                 0                     0  
1                                 1                     0  
2                                 8                     2  
3                                 1                     0  
4                                 0                     0

In [113]:
#Делаем распределение по темам в зависимости от общего количества книг, купленных пользователем

In [114]:
for i in tqdm(range(len(tab_theme_usersForX))):
    share=tab_theme_usersForX.iloc[i,1:]/sum(tab_theme_usersForX.iloc[i,1:])
    tab_theme_usersForX.iloc[i,1:] = share * 10  

100%|█████████████████████████████████████████████████████████████████████████████| 7835/7835 [00:24<00:00, 322.14it/s]


In [115]:
tab_theme_usersForX.head()

OrderCustomerID  allagetrendbooksnonfiction  игрыдосугирукоделие  \
0           32185                         0.0                  0.0   
1           32186                         0.0                  0.0   
2           32188                         0.0                  0.0   
3           32190                         0.0                  0.0   
4           32192                         0.0                  0.0   

   книгидлявзрослых  познавательнаялитературадошкольники  \
0               0.0                             0.000000   
1               0.0                             5.000000   
2               0.0                             1.333333   
3               0.0                             0.000000   
4               0.0                            10.000000   

   познавательнаялитературашкольники  психологияивоспитаниедетей  \
0                                0.0                         0.0   
1                                0.0                         0.0   
2                                0.0                         0.0   
3                                0.0                         0.0   
4                                0.0                         0.0   

   развлекательнаялитература  учебнаялитературашкольники  \
0                       0.00                        10.0   
1                       3.75                         0.0   
2                       2.00                         0.0   
3                       5.00                         0.0   
4                       0.00                         0.0   

   художественнаялитературадлядетей  энциклопедиидлядетей  
0                          0.000000              0.000000  
1                          1.250000              0.000000  
2                          5.333333              1.333333  
3                          5.000000              0.000000  
4                          0.000000              0.000000

In [116]:
#Редактируем название темы

In [117]:
tab_forX_books['theme'] = [x.replace(' ','') for x in tab_forX_books['theme']]
tab_forX_books['theme'] = [x.replace(',','') for x in tab_forX_books['theme']]
tab_forX_books['theme'] = [x.replace('-','') for x in tab_forX_books['theme']]
tab_forX_books['theme'] = [x.replace('(','') for x in tab_forX_books['theme']]
tab_forX_books['theme'] = [x.replace(')','') for x in tab_forX_books['theme']]
tab_forX_books['theme'] = [x.replace('+','') for x in tab_forX_books['theme']]

In [118]:
theme_predict = tab_forX_books[['OrderCustomerID', 'theme']].merge(tab_theme_usersForX, on = 'OrderCustomerID', how = 'left')

In [119]:
theme_predict.head()

OrderCustomerID             theme  allagetrendbooksnonfiction  \
0           55301  Книгидлявзрослых                    0.000000   
1           60253  Книгидлявзрослых                    0.000000   
2           58055  Книгидлявзрослых                    0.000000   
3           43760  Книгидлявзрослых                    0.000000   
4           36489  Книгидлявзрослых                    0.044053   

   игрыдосугирукоделие  книгидлявзрослых  познавательнаялитературадошкольники  \
0             0.000000               0.0                             7.142857   
1             0.000000               0.0                             0.714286   
2             0.833333               0.0                             2.500000   
3             0.526316               0.0                             4.210526   
4             0.176211               0.0                             3.436123   

   познавательнаялитературашкольники  психологияивоспитаниедетей  \
0                                0.0                    0.000000   
1                                0.0                    0.000000   
2                                0.0                    0.000000   
3                                0.0                    0.000000   
4                                0.0                    0.044053   

   развлекательнаялитература  учебнаялитературашкольники  \
0                   0.000000                    0.000000   
1                   1.428571                    0.000000   
2                   2.500000                    0.000000   
3                   3.157895                    1.578947   
4                   2.378855                    1.453744   

   художественнаялитературадлядетей  энциклопедиидлядетей  
0                          0.000000              2.857143  
1                          7.142857              0.714286  
2                          4.166667              0.000000  
3                          0.526316              0.000000  
4                          2.246696              0.220264

In [120]:
theme_X = theme_predict[['OrderCustomerID']+vectorizer_c.get_feature_names()]

In [121]:
theme_y = theme_predict['theme']

In [122]:
X_train_theme, X_test_theme, y_train_theme, y_test_theme = train_test_split(theme_X, theme_y ,
                                                                            test_size = 0.6, 
                                                                            random_state = 42)

In [123]:
X_train_theme_for_ac, X_test_theme_for_ac, y_train_theme_for_ac, y_test_theme_for_ac = train_test_split(theme_X[:one], 
                                                                                                        theme_y[:one], 
                                                                                                        test_size = 0.4, 
                                                                                                        random_state = 42)

In [124]:
X_train_theme_surp = X_train_theme_for_ac[['OrderCustomerID', vectorizer_c.get_feature_names()[0]]]
X_train_theme_surp['theme'] = vectorizer_c.get_feature_names()[0]
X_train_theme_surp['rating'] = X_train_theme_surp[vectorizer_c.get_feature_names()[0]]
for i in range(1,len(vectorizer_c.get_feature_names())):
    X_train_theme_surp_next = X_train_theme_for_ac[['OrderCustomerID', vectorizer_c.get_feature_names()[i]]]
    X_train_theme_surp_next['theme'] = vectorizer_c.get_feature_names()[i]
    X_train_theme_surp_next['rating'] = X_train_theme_surp_next[vectorizer_c.get_feature_names()[i]]
    X_train_theme_surp = pd.concat([X_train_theme_surp, X_train_theme_surp_next], axis = 0, ignore_index = True)
X_train_theme_surp.drop(vectorizer_c.get_feature_names(),axis = 1, inplace = True)
X_train_theme_surp = X_train_theme_surp[['OrderCustomerID','theme', 'rating']]

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

In [125]:
from surprise import SVD
from surprise import Reader, Dataset
reader = Reader(rating_scale=(1,10))
X_train_theme_surp = Dataset.load_from_df(X_train_theme_surp, reader)
X_train_theme_surp = X_train_theme_surp.build_full_trainset()
algo = SVD()
algo.fit(X_train_theme_surp)

In [126]:
theme_pred = []
for i in X_test_theme['OrderCustomerID'].values.tolist():
    probs = []
    for j in X_test_theme.columns.tolist()[1:]:
        probs.append(algo.predict(uid = i,iid = j, r_ui = 5)[3])
    theme_pred.append(probs)

In [127]:
algo.predict(uid = '34760',iid = 'познавательнаялитературадошкольники')

Prediction(uid='34760', iid='познавательнаялитературадошкольники', r_ui=None, est=3.634230192514149, details={'was_impossible': False})

In [128]:
theme_pred_prob = np.array([x/sum(i) for i in theme_pred for x in i]).reshape(-1,10)

In [129]:
theme_pred_prob

array([[0.05232105, 0.05232105, 0.05232105, ..., 0.05232105, 0.05232105,
        0.05232105],
       [0.05457259, 0.05457259, 0.05457259, ..., 0.05457259, 0.05457259,
        0.05457259],
       [0.05656161, 0.05656161, 0.05656161, ..., 0.05656161, 0.3077251 ,
        0.05656161],
       ...,
       [0.06238131, 0.06238131, 0.06238131, ..., 0.06238131, 0.21683949,
        0.06238131],
       [0.05788907, 0.05788907, 0.05788907, ..., 0.14111696, 0.05788907,
        0.05788907],
       [0.05263158, 0.05263158, 0.05263158, ..., 0.05263158, 0.05263158,
        0.05263158]])

In [130]:
theme_factor = pd.DataFrame(theme_pred_prob)

In [131]:
theme_factor.iloc[0]

0    0.052321
1    0.052321
2    0.052321
3    0.190147
4    0.052321
5    0.052321
6    0.391285
7    0.052321
8    0.052321
9    0.052321
Name: 0, dtype: float64

In [132]:
theme_pred_for_ac = []
for i in X_test_theme_for_ac['OrderCustomerID'].values.tolist():
    probs = []
    for j in X_test_theme_for_ac.columns.tolist()[1:]:
        probs.append(algo.predict(uid = i,iid = j, r_ui = 5)[3])
    theme_pred_for_ac.append(probs)
theme_pred_ac_prob = np.array([x/sum(i) for i in theme_pred_for_ac for x in i]).reshape(-1,10)

In [133]:
accuracy = []
for i in range(len(X_test_theme_for_ac)):
    max_test = X_test_theme_for_ac.iloc[i].values[1:].tolist().index(max(X_test_theme_for_ac.iloc[i].values[1:]))
    max_pred = pd.DataFrame(theme_pred_ac_prob).iloc[i].values.tolist().index(max(pd.DataFrame(theme_pred_ac_prob).iloc[i].values))
    if max_test == max_pred:
        accuracy.append(1)
    else:
        accuracy.append(0)
print(sum(accuracy)/len(X_test_theme_for_ac))

0.957585044437634


In [134]:
#Accuracy по предсказанию темы составляет 96%

In [135]:
theme_factor.head()

0         1         2         3         4         5         6  \
0  0.052321  0.052321  0.052321  0.190147  0.052321  0.052321  0.391285   
1  0.054573  0.054573  0.054573  0.502952  0.054573  0.054573  0.060468   
2  0.056562  0.056562  0.056562  0.198440  0.056562  0.056562  0.097903   
3  0.061380  0.061380  0.061380  0.378118  0.061380  0.061380  0.130840   
4  0.060435  0.090750  0.060435  0.378426  0.060435  0.060435  0.060435   

          7         8         9  
0  0.052321  0.052321  0.052321  
1  0.054573  0.054573  0.054573  
2  0.056562  0.307725  0.056562  
3  0.061380  0.061380  0.061380  
4  0.060435  0.060435  0.107777

In [136]:
#Теги

In [137]:
tab_annotation_usersForX = tabprep(tab_factor, 'annotation', 'OrderCustomerID')

100%|████████████████████████████████████████████████████████████████████████████| 16895/16895 [10:06<00:00, 27.85it/s]


In [138]:
tab_annotation_usersForX = tab_annotation_usersForX[['OrderCustomerID','annotation']]

In [139]:
tab_annotation_usersForX.drop_duplicates(inplace = True)
tab_annotation_usersForX.reset_index(inplace = True)
tab_annotation_usersForX.drop('index', axis = 1, inplace = True)

In [140]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [141]:
vectorizer_annot = TfidfVectorizer(ngram_range = (1,1))
tfidf_annot = vectorizer_annot.fit_transform(tab_annotation_usersForX['annotation'])

In [142]:
tab_annotation_usersForX['annotation2'] = [x.split(' ') for x  in tab_annotation_usersForX['annotation']]

In [143]:
import multiprocessing

In [144]:
cores = multiprocessing.cpu_count()

In [145]:
cores

4

In [146]:
import time

In [147]:
import logging #для отображения состояния
logging.basicConfig(format="%(levelname)s - %(asctime)s: %(message)s", datefmt = '%H:%M:%S', level = logging.INFO)

In [148]:
#Считаем word2vec

In [149]:
from gensim.models import Word2Vec
model = Word2Vec(min_count = 20,
                     window = 5,
                     size = 100,
                     sample = 6e-5, 
                     alpha = 0.03, 
                     min_alpha = 0.0007, 
                     workers = cores-1)

INFO - 14:32:01: 'pattern' package not found; tag filters are not available for English
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\gensim\models\base_any2vec.py:743: UserWarning: C extension not loaded, training will be slow. Install a C compiler and reinstall gensim for fast training.
  "C extension not loaded, training will be slow. "


In [150]:
%%time
model.build_vocab(sentences = tab_annotation_usersForX['annotation2'].values.tolist()[:1000], 
                  progress_per = 10000)

model.train(sentences = tab_annotation_usersForX['annotation2'].values.tolist()[:1000],
            total_examples = 1000, 
            epochs = 10, 
            report_delay = 1)


INFO - 14:32:01: collecting all words and their counts
INFO - 14:32:01: PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
INFO - 14:32:01: collected 7352 word types from a corpus of 763529 raw words and 1000 sentences
INFO - 14:32:01: Loading a fresh vocabulary
INFO - 14:32:01: effective_min_count=20 retains 4034 unique words (54% of original 7352, drops 3318)
INFO - 14:32:01: effective_min_count=20 leaves 737512 word corpus (96% of original 763529, drops 26017)
INFO - 14:32:01: deleting the raw counts dictionary of 7352 items
INFO - 14:32:01: sample=6e-05 downsamples 1215 most-common words
INFO - 14:32:01: downsampling leaves estimated 350644 word corpus (47.5% of prior 737512)
INFO - 14:32:01: estimated required memory for 4034 words and 100 dimensions: 5244200 bytes
INFO - 14:32:01: resetting layer weights
INFO - 14:32:01: training model with 3 workers on 4034 vocabulary and 100 features, using sg=0 hs=0 sample=6e-05 negative=5 window=5
INFO - 14:32:07: EPOCH 1 - PRO

INFO - 14:36:18: EPOCH 2 - PROGRESS: at 35.60% examples, 1662 words/s, in_qsize 6, out_qsize 0
INFO - 14:36:21: EPOCH 2 - PROGRESS: at 37.20% examples, 1661 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:26: EPOCH 2 - PROGRESS: at 40.00% examples, 1664 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:28: EPOCH 2 - PROGRESS: at 41.50% examples, 1717 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:34: EPOCH 2 - PROGRESS: at 42.10% examples, 1649 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:36: EPOCH 2 - PROGRESS: at 45.70% examples, 1717 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:41: EPOCH 2 - PROGRESS: at 47.60% examples, 1668 words/s, in_qsize 6, out_qsize 0
INFO - 14:36:42: EPOCH 2 - PROGRESS: at 49.20% examples, 1682 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:49: EPOCH 2 - PROGRESS: at 51.50% examples, 1664 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:52: EPOCH 2 - PROGRESS: at 52.50% examples, 1708 words/s, in_qsize 5, out_qsize 0
INFO - 14:36:56: EPOCH 2 - PROGRESS: at 53.80% exa

INFO - 14:41:11: EPOCH 3 - PROGRESS: at 81.80% examples, 1663 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:12: EPOCH 3 - PROGRESS: at 83.80% examples, 1676 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:19: EPOCH 3 - PROGRESS: at 85.30% examples, 1684 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:20: EPOCH 3 - PROGRESS: at 88.40% examples, 1727 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:27: EPOCH 3 - PROGRESS: at 88.80% examples, 1685 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:28: EPOCH 3 - PROGRESS: at 90.60% examples, 1726 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:30: EPOCH 3 - PROGRESS: at 91.40% examples, 1720 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:32: EPOCH 3 - PROGRESS: at 92.10% examples, 1712 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:37: EPOCH 3 - PROGRESS: at 92.20% examples, 1696 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:39: EPOCH 3 - PROGRESS: at 94.30% examples, 1720 words/s, in_qsize 5, out_qsize 0
INFO - 14:41:40: EPOCH 3 - PROGRESS: at 94.70% exa

INFO - 14:45:28: EPOCH 5 - PROGRESS: at 7.40% examples, 1430 words/s, in_qsize 5, out_qsize 0
INFO - 14:45:35: EPOCH 5 - PROGRESS: at 8.80% examples, 1360 words/s, in_qsize 5, out_qsize 0
INFO - 14:45:43: EPOCH 5 - PROGRESS: at 13.70% examples, 1422 words/s, in_qsize 6, out_qsize 0
INFO - 14:45:50: EPOCH 5 - PROGRESS: at 17.50% examples, 1513 words/s, in_qsize 5, out_qsize 0
INFO - 14:45:51: EPOCH 5 - PROGRESS: at 18.70% examples, 1590 words/s, in_qsize 5, out_qsize 0
INFO - 14:45:56: EPOCH 5 - PROGRESS: at 20.40% examples, 1570 words/s, in_qsize 5, out_qsize 0
INFO - 14:45:58: EPOCH 5 - PROGRESS: at 21.80% examples, 1615 words/s, in_qsize 6, out_qsize 0
INFO - 14:45:59: EPOCH 5 - PROGRESS: at 22.20% examples, 1678 words/s, in_qsize 6, out_qsize 0
INFO - 14:46:03: EPOCH 5 - PROGRESS: at 22.50% examples, 1610 words/s, in_qsize 5, out_qsize 0
INFO - 14:46:05: EPOCH 5 - PROGRESS: at 25.00% examples, 1684 words/s, in_qsize 5, out_qsize 0
INFO - 14:46:10: EPOCH 5 - PROGRESS: at 26.20% examp

INFO - 14:50:28: EPOCH 6 - PROGRESS: at 55.20% examples, 1672 words/s, in_qsize 6, out_qsize 0
INFO - 14:50:34: EPOCH 6 - PROGRESS: at 58.60% examples, 1667 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:35: EPOCH 6 - PROGRESS: at 60.80% examples, 1680 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:41: EPOCH 6 - PROGRESS: at 63.90% examples, 1662 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:43: EPOCH 6 - PROGRESS: at 66.80% examples, 1710 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:48: EPOCH 6 - PROGRESS: at 67.50% examples, 1675 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:50: EPOCH 6 - PROGRESS: at 71.00% examples, 1712 words/s, in_qsize 5, out_qsize 0
INFO - 14:50:56: EPOCH 6 - PROGRESS: at 72.10% examples, 1677 words/s, in_qsize 5, out_qsize 0
INFO - 14:51:03: EPOCH 6 - PROGRESS: at 75.10% examples, 1671 words/s, in_qsize 5, out_qsize 0
INFO - 14:51:05: EPOCH 6 - PROGRESS: at 75.60% examples, 1713 words/s, in_qsize 6, out_qsize 0
INFO - 14:51:11: EPOCH 6 - PROGRESS: at 77.80% exa

INFO - 14:55:23: worker thread finished; awaiting finish of 2 more threads
INFO - 14:55:25: EPOCH 7 - PROGRESS: at 98.50% examples, 1685 words/s, in_qsize 1, out_qsize 1
INFO - 14:55:25: worker thread finished; awaiting finish of 1 more threads
INFO - 14:55:25: worker thread finished; awaiting finish of 0 more threads
INFO - 14:55:25: EPOCH - 7 : training on 763529 raw words (350724 effective words) took 205.5s, 1707 effective words/s
INFO - 14:55:31: EPOCH 8 - PROGRESS: at 1.10% examples, 568 words/s, in_qsize 5, out_qsize 0
INFO - 14:55:32: EPOCH 8 - PROGRESS: at 4.90% examples, 1556 words/s, in_qsize 6, out_qsize 0
INFO - 14:55:37: EPOCH 8 - PROGRESS: at 6.60% examples, 1246 words/s, in_qsize 5, out_qsize 0
INFO - 14:55:38: EPOCH 8 - PROGRESS: at 6.70% examples, 1200 words/s, in_qsize 5, out_qsize 0
INFO - 14:55:39: EPOCH 8 - PROGRESS: at 8.70% examples, 1659 words/s, in_qsize 5, out_qsize 0
INFO - 14:55:45: EPOCH 8 - PROGRESS: at 8.80% examples, 1399 words/s, in_qsize 5, out_qsize 

INFO - 15:00:08: EPOCH 9 - PROGRESS: at 41.50% examples, 1685 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:13: EPOCH 9 - PROGRESS: at 42.10% examples, 1643 words/s, in_qsize 6, out_qsize 0
INFO - 15:00:14: EPOCH 9 - PROGRESS: at 44.20% examples, 1672 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:16: EPOCH 9 - PROGRESS: at 45.70% examples, 1689 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:20: EPOCH 9 - PROGRESS: at 47.60% examples, 1663 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:22: EPOCH 9 - PROGRESS: at 49.20% examples, 1655 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:28: EPOCH 9 - PROGRESS: at 51.50% examples, 1657 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:29: EPOCH 9 - PROGRESS: at 52.40% examples, 1673 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:32: EPOCH 9 - PROGRESS: at 52.50% examples, 1687 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:35: EPOCH 9 - PROGRESS: at 53.80% examples, 1674 words/s, in_qsize 5, out_qsize 0
INFO - 15:00:37: EPOCH 9 - PROGRESS: at 55.80% exa

INFO - 15:04:50: EPOCH 10 - PROGRESS: at 81.80% examples, 1670 words/s, in_qsize 5, out_qsize 0
INFO - 15:04:52: EPOCH 10 - PROGRESS: at 81.90% examples, 1701 words/s, in_qsize 6, out_qsize 0
INFO - 15:04:53: EPOCH 10 - PROGRESS: at 83.90% examples, 1714 words/s, in_qsize 5, out_qsize 0
INFO - 15:04:58: EPOCH 10 - PROGRESS: at 85.30% examples, 1693 words/s, in_qsize 5, out_qsize 0
INFO - 15:04:59: EPOCH 10 - PROGRESS: at 86.50% examples, 1703 words/s, in_qsize 5, out_qsize 0
INFO - 15:05:01: EPOCH 10 - PROGRESS: at 88.40% examples, 1714 words/s, in_qsize 5, out_qsize 0
INFO - 15:05:05: EPOCH 10 - PROGRESS: at 88.80% examples, 1695 words/s, in_qsize 5, out_qsize 0
INFO - 15:05:07: EPOCH 10 - PROGRESS: at 89.80% examples, 1703 words/s, in_qsize 6, out_qsize 0
INFO - 15:05:08: EPOCH 10 - PROGRESS: at 90.60% examples, 1703 words/s, in_qsize 5, out_qsize 0
INFO - 15:05:12: EPOCH 10 - PROGRESS: at 92.10% examples, 1703 words/s, in_qsize 5, out_qsize 0
INFO - 15:05:17: EPOCH 10 - PROGRESS: at

Wall time: 33min 30s


In [317]:
model.most_similar('буква')

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: DeprecationWarning: Call to deprecated `most_similar` (Method will be removed in 4.0.0, use self.wv.most_similar() instead).
  """Entry point for launching an IPython kernel.


[('писать', 0.8108351230621338),
 ('закорючка', 0.7331889271736145),
 ('цифра', 0.7204335927963257),
 ('определо', 0.719122588634491),
 ('дополнительный', 0.7157763242721558),
 ('азбука', 0.7072781920433044),
 ('научиться', 0.7060977816581726),
 ('крючок', 0.7047520279884338),
 ('стирать', 0.6999059319496155),
 ('письменный', 0.6969338655471802)]

In [152]:
words = list(model.wv.vocab)
print(words)

['сложность', 'произношение', 'звук', 'распространённый', 'проблема', 'ребёнок', 'языковой', 'гимнастика', 'упражнение', 'мочь', 'утомительный', 'передовой', 'авторский', 'методика', 'галанов', 'известный', 'логопед', 'психолог', 'директор', 'лаборатория', 'психологический', 'безопасность', 'международный', 'академия', 'наука', 'основанный', 'достижение', 'нейрофизиология', 'помощь', 'дошкольник', 'легко', 'отработать', 'процесс', 'лой', 'игра', 'коробка', 'тот', 'комплект', 'карточка', 'жетон', 'играть', 'речевой', 'пошаговый', 'гид', 'родитель', 'загадка', 'скороговорка', 'чистоговорка', 'считалка', 'набор', 'подходить', 'занятие', 'один', 'группа', 'весёлый', 'найти', 'поучительный', 'история', 'федя', 'научиться', 'пользоваться', 'ложка', 'самостоятельно', 'пример', 'главный', 'герой', 'освоить', 'необходимый', 'жизненный', 'навык', 'забавный', 'стих', 'рисунок', 'больший', 'количество', 'деталь', 'непременно', 'совет', 'использовать', 'книжка', 'развивающий', 'показать', 'предложи

In [153]:
#Формируем матрицу слово-вектор
word_matrix = []
for j in tqdm(range(len(vectorizer_annot.get_feature_names()))):
    try:
        res = model[vectorizer_annot.get_feature_names()[j]]
    except:
        res = np.zeros(100)
    word_matrix.append(res)

  0%|                                                                                         | 0/8332 [00:00<?, ?it/s]C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """
100%|█████████████████████████████████████████████████████████████████████████████| 8332/8332 [00:35<00:00, 233.94it/s]


In [154]:
tags_users = np.dot(tfidf_annot.toarray(),np.array(word_matrix))

In [155]:
tags_users.shape

(7835, 100)

In [156]:
tags_users = [list(x) for x in tags_users]

In [157]:
tab_annotation_usersForX['tag_users'] = tags_users

In [158]:
len(tags_users[0])

100

In [159]:
tab_annotation_usersForX.head()

OrderCustomerID                                         annotation  \
0           32185  сложность произношение звук распространённый п...   
1           32186  весёлый поучительный история федя научиться по...   
2           32188  самопиар привет старший брат книга ты ужасно у...   
3           32190  весёлый поучительный история федя научиться хо...   
4           32192  заниматься дом детский сад мой один открытие к...   

                                         annotation2  \
0  [сложность, произношение, звук, распространённ...   
1  [весёлый, поучительный, история, федя, научить...   
2  [самопиар, привет, старший, брат, книга, ты, у...   
3  [весёлый, поучительный, история, федя, научить...   
4  [заниматься, дом, детский, сад, мой, один, отк...   

                                           tag_users  
0  [-1.930130339456874, -4.020016883131021, -7.01...  
1  [-9.70517305853589, -3.956316631531351, -5.951...  
2  [-7.316465662939966, -0.38439110513304225, -14...  
3  [-4.230994606018826, -3.1478094123117217, -4.2...  
4  [-3.243014629919552, 0.13167887172947096, -6.7...

In [160]:
tfidf_tags_books = vectorizer_annot.transform(tab_forX_books['annotation'])

In [161]:
tags_books = np.dot(tfidf_tags_books.toarray(),np.array(word_matrix))

In [162]:
tags_books = [list(x) for x in tags_books]

In [163]:
tab_forX_books['tag_books'] = tags_books

In [164]:
tab_forX_books = tab_forX_books.merge(tab_annotation_usersForX[['OrderCustomerID', 'tag_users']], how ='left', on ='OrderCustomerID')

In [165]:
tab_forX_books.head()

OrderID  OrderTotalPrice                     OrderDate  OrderSiteID  \
0   157260             3000 2017-12-20 17:19:59.411723600            1   
1   111969             3659 2017-05-11 21:07:56.180847000            1   
2    96054             1158 2017-10-18 13:05:33.052566400            1   
3    95983             2908 2017-10-18 16:22:12.434237800            1   
4    97245            10272 2017-10-06 22:42:31.633052100            1   

   OrderItemUnitCount                  isbn  \
0                   1  978-5-906824-45-5      
1                   1  978-5-906824-45-5      
2                   1  978-5-906824-45-5      
3                   1  978-5-906824-45-5      
4                   1  978-5-906824-45-5      

                                  title  \
0  Раскраска-антистресс. Волшебные миры   
1  Раскраска-антистресс. Волшебные миры   
2  Раскраска-антистресс. Волшебные миры   
3  Раскраска-антистресс. Волшебные миры   
4  Раскраска-антистресс. Волшебные миры   

                                          annotation             title.1  \
0  книга раскраска дарить самый ценный жизнь врем...  Книги для взрослых   
1  книга раскраска дарить самый ценный жизнь врем...  Книги для взрослых   
2  книга раскраска дарить самый ценный жизнь врем...  Книги для взрослых   
3  книга раскраска дарить самый ценный жизнь врем...  Книги для взрослых   
4  книга раскраска дарить самый ценный жизнь врем...  Книги для взрослых   

   authorid  ...   age               CustomerCreated day_after_reg  \
0     269.0  ...  7-11 2016-10-16 23:12:39.350475400           429   
1     269.0  ...  7-11 2016-05-30 23:38:06.588004500           345   
2     269.0  ...  7-11 2016-10-21 15:14:18.344162200           361   
3     269.0  ...  7-11 2016-09-30 16:39:02.134639900           382   
4     269.0  ...  7-11 2016-12-25 02:06:37.927011600           285   

              theme  cus-ergroup OrderCustomerID  group buyornot  \
0  Книгидлявзрослых      55301 2           55301      2      1.0   
1  Книгидлявзрослых      60253 2           60253      2      1.0   
2  Книгидлявзрослых      58055 2           58055      2      1.0   
3  Книгидлявзрослых      43760 2           43760      2      1.0   
4  Книгидлявзрослых      36489 2           36489      2      1.0   

                                           tag_books  \
0  [-3.0193062832547084, -1.7527038823225847, -1....   
1  [-3.0193062832547084, -1.7527038823225847, -1....   
2  [-3.0193062832547084, -1.7527038823225847, -1....   
3  [-3.0193062832547084, -1.7527038823225847, -1....   
4  [-3.0193062832547084, -1.7527038823225847, -1....   

                                           tag_users  
0  [-3.7788323169168008, -1.308015492543004, -6.4...  
1  [-5.0076560555344996, -0.6974739584024089, -10...  
2  [-7.24312941521765, -0.6589608608804103, -6.73...  
3  [-7.061769907971466, -3.704476284790277, -12.3...  
4  [-11.1264889382437, -7.065435838317836, -22.95...  

[5 rows x 27 columns]

In [166]:
target = tab_forX_books['buyornot']

In [167]:
X_train_tag, X_test_tag, y_train_tag, y_test_tag = train_test_split(tab_forX_books, target, test_size = 0.6, random_state = 42)

In [168]:
from scipy.spatial.distance import cosine

In [169]:
#Вариант 1
#Теги буду браться не целыми векторами, а только одним числом- косинусным расстоянием между вектором юзера и пользователя

In [170]:
factor_tag = []
for i in tqdm(range(len(X_test_tag))):
    factor_tag.append(cosine(X_test_tag['tag_books'].values.tolist()[i],X_test_tag['tag_users'].values.tolist()[i]))

100%|███████████████████████████████████████████████████████████████████████████| 89187/89187 [05:47<00:00, 256.72it/s]


In [171]:
#Формируем таблицу, состоящую из фактора возраста, темы, тегов. 
#Фактор возраста и темы - предсказания на тестовых данных (тест отделялся при обучении модели по теме и возрасту)
#теги взяты специально только для данной части данных

In [172]:
X = pd.concat([theme_factor, age_features, pd.DataFrame(factor_tag)], axis = 1, ignore_index = True)

In [173]:
X_train_pr, X_test_pr, y_train_pr, y_test_pr=train_test_split(X, y_test_tag, test_size = 0.2, random_state = 42)

In [174]:
X_train_pr_test, X_test_pr_test = train_test_split(X_test_tag, test_size = 0.2, random_state = 42)

In [181]:
data = X_train_pr
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

Accuracy составляет 0.6028
Precision составляет 0.6473


In [182]:
#Для создания словаря пользователь- рекомендации в порядке убывания (по тестовым данным)
def test_recommendations(pred):
    
    X_test_rec = X_test_pr_test.copy()
    X_test_rec['y_pred'] = pred
    X_test_rec1 = X_test_rec[['OrderCustomerID', 'isbn', 'y_pred']].sort_values(by = 'y_pred', ascending=False)
    customers_for_test = set(X_test_rec['OrderCustomerID'])
    preds = {}
    for i in customers_for_test:
        X_test_rec_cus = X_test_rec1[X_test_rec1['OrderCustomerID'] == i]
        res = X_test_rec_cus['isbn'].tolist()
        preds[i] = res
    return preds

In [183]:
for_test = test_recommendations(y_pred)

In [184]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:26<00:00, 24.43it/s]


In [185]:
metric

(0.25320580176705776,
 [0.1,
  0.0,
  0.0,
  0.1,
  0.2,
  0.1,
  0.3333333333333333,
  0.15666666666666668,
  0.0,
  0.1,
  0.1,
  0.1,
  0.1,
  0.1,
  0.2,
  0.0,
  0.1,
  0.0,
  0.1,
  0.0,
  0.16666666666666666,
  0.025,
  0.0,
  0.1,
  0.0,
  0.0,
  0.03333333333333333,
  0.2,
  0.11666666666666665,
  0.05,
  0.2,
  0.1,
  0.1,
  0.2,
  0.05,
  0.0,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.05,
  0.05,
  0.1,
  0.03333333333333333,
  0.0,
  0.16666666666666666,
  0.0,
  0.1,
  0.2,
  6.460952380952381,
  0.0,
  0.16666666666666666,
  0.8533333333333333,
  0.2,
  0.3333333333333333,
  0.05,
  0.1,
  0.0,
  0.21666666666666665,
  0.1,
  0.1,
  0.27999999999999997,
  0.0,
  0.05,
  1.7996825396825398,
  0.1,
  0.21666666666666665,
  0.3333333333333333,
  0.21666666666666665,
  0.05,
  0.1,
  0.0,
  0.1,
  0.0,
  0.0,
  0.0,
  0.0,
  0.1,
  0.05,
  0.1,
  0.0,
  0.5277777777777778,
  0.0,
  0.1,
  0.05,
  0.1,
  0.0,
  0.15666666666666668,
  0.1,
  0.1,
  0.0,
  0.33

In [ ]:
#Mean average precision at k для варианта 1 составляет 25%

In [ ]:
#mean average precision at k получился гораздо лучше, чем при рекомендации топ-продаж

In [ ]:
#Варитант 2. Берем не косинусное расстояние, а вектора полностью

In [186]:
factor_tag = [list(X_test_tag['tag_books'].values.tolist()[i]) + list(X_test_tag['tag_users'].values.tolist()[i]) for i in range(len(X_test_tag))]

In [187]:
X = pd.concat([theme_factor, age_features, pd.DataFrame(factor_tag)], axis = 1, ignore_index = True)

In [188]:
X_train_pr, X_test_pr, y_train_pr, y_test_pr = train_test_split(X, y_test_tag, test_size = 0.2, random_state = 42)

In [189]:
data = X_train_pr
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


Accuracy составляет 0.9304
Precision составляет 0.9215


In [190]:
for_test = test_recommendations(y_pred)

In [191]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:20<00:00, 24.45it/s]


In [192]:
metric

(0.3691368843350655,
 [0.1,
  0.0,
  0.0,
  0.1,
  0.2,
  0.1,
  0.3333333333333333,
  0.3,
  0.0,
  0.1,
  0.2,
  0.1,
  0.1,
  0.1,
  0.2,
  0.0,
  0.1,
  0.0,
  0.1,
  0.0,
  0.2,
  0.1,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.2,
  0.2,
  0.1,
  0.2,
  0.1,
  0.1,
  0.2,
  0.1,
  0.0,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.1,
  0.1,
  0.1,
  0.0,
  0.2,
  0.0,
  0.1,
  0.2,
  11.865396825396825,
  0.0,
  0.2,
  0.8533333333333333,
  0.2,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.1,
  0.1,
  0.3333333333333333,
  0.0,
  0.1,
  2.097777777777778,
  0.1,
  0.3333333333333333,
  0.3333333333333333,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.1,
  0.0,
  0.0,
  0.0,
  0.0,
  0.1,
  0.1,
  0.1,
  0.0,
  0.8533333333333333,
  0.0,
  0.1,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.2,
  0.2,
  0.15,
  0.1,
  0.2,
  0.1,
  0.3333333333333333,
  0.3333333333333333,
  0.0,
  0.2,
  0.2,
  0.0

In [ ]:
#Mean average precision at k для варианта 2 составляет 37%

In [ ]:
#Вариант 2 получился лучше, чем вариант 1

In [193]:
#Вариант 3. Делаем усеченное SVD на веторах юзера и пользователя
from sklearn.decomposition import TruncatedSVD
svd = TruncatedSVD(n_components = 10, algorithm = 'randomized', n_iter = 5, random_state = None, tol = 0.0)

In [194]:
svd_tags_train = svd.fit_transform(X_train_pr.iloc[:,-200:])
svd_tags_test = svd.transform(X_test_pr.iloc[:,-200:])

In [195]:
X_train_pr.reset_index(inplace=True)
X_train_pr.drop('index', axis=1, inplace=True)
X_test_pr.reset_index(inplace=True)
X_test_pr.drop('index', axis=1, inplace=True)

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\frame.py:3940: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


In [196]:
X_train_pr = pd.concat([X_train_pr.iloc[:,:-200], pd.DataFrame(svd_tags_train)], axis=1, ignore_index=True)

In [197]:
X_test_pr = pd.concat([X_test_pr.iloc[:,:-200], pd.DataFrame(svd_tags_test)], axis=1, ignore_index=True)

In [199]:
data = X_train_pr
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


Accuracy составляет 0.8903
Precision составляет 0.9136


In [200]:
for_test = test_recommendations(y_pred)

In [201]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:23<00:00, 24.24it/s]


In [202]:
metric

(0.3300546486038936,
 [0.1,
  0.0,
  0.0,
  0.1,
  0.2,
  0.1,
  0.3333333333333333,
  0.3,
  0.0,
  0.1,
  0.2,
  0.1,
  0.1,
  0.1,
  0.2,
  0.0,
  0.05,
  0.0,
  0.1,
  0.0,
  0.16666666666666666,
  0.1,
  0.0,
  0.1,
  0.0,
  0.0,
  0.05,
  0.2,
  0.2,
  0.1,
  0.2,
  0.1,
  0.1,
  0.2,
  0.1,
  0.0,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.1,
  0.1,
  0.1,
  0.1,
  0.0,
  0.2,
  0.0,
  0.1,
  0.2,
  11.865396825396825,
  0.0,
  0.2,
  0.8533333333333333,
  0.2,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.1,
  0.1,
  0.3333333333333333,
  0.0,
  0.1,
  1.3104761904761904,
  0.1,
  0.3333333333333333,
  0.3333333333333333,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.1,
  0.0,
  0.0,
  0.0,
  0.0,
  0.1,
  0.1,
  0.1,
  0.0,
  0.8533333333333333,
  0.0,
  0.1,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.1,
  0.1,
  0.0,
  0.3333333333333333,
  0.16666666666666666,
  0.2,
  0.2,
  0.1,
  0.2,
  0.1,
  0.3333333333333333,
  0.3333333333

In [ ]:
#Mean average precision at k для варианта 3 составляет 33%

In [ ]:
#Baseline только на кастомерах теста- уточнение

In [203]:
customers_for_test = list(set(X_test_pr_test['OrderCustomerID']))

In [204]:
#делаем список книг, которые не покупались для каждого пользователя
X_top_books = {}
for i in tqdm(customers_for_test):
    x_top = []
    for j in books:
        if FORtop[j][i] == 0:
            x_top.append(j)
    X_top_books[i] = x_top

100%|██████████████████████████████████████████████████████████████████████████████| 5828/5828 [01:05<00:00, 89.02it/s]


In [205]:
metric = mean_av_precision_at_k(X_top_books, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:32<00:00, 23.78it/s]


In [206]:
metric

(0.01390763391835801,
 [0.0,
  0.02,
  0.0,
  0.025,
  0.02,
  0.0,
  0.0,
  0.13444444444444445,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.0,
  0.0125,
  0.0,
  0.01,
  0.0,
  0.0,
  0.0,
  0.0,
  0.065,
  0.0,
  0.0,
  0.0,
  0.0,
  0.01,
  0.0,
  0.0,
  0.1,
  0.0,
  0.0,
  0.0,
  0.02,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.016666666666666666,
  0.0,
  0.016666666666666666,
  0.014285714285714285,
  0.01,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.05,
  0.0,
  0.025,
  0.0125,
  0.0,
  0.0,
  0.014285714285714285,
  0.0,
  0.0,
  0.0,
  0.02,
  0.0,
  0.0,
  0.0,
  0.014285714285714285,
  0.04857142857142857,
  0.025,
  0.0125,
  0.0,
  0.014285714285714285,
  0.0,
  0.0,
  0.07222222222222222,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.125,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0125,
  0.02,
  0.0,
  0.0,
  0.0,
  0.0,
  0.0125,
  0.125,
 

In [ ]:
#Mean average precision at k для уточненного baseline составляет 1,4%

In [ ]:
#Вывод - вариант 2 получился самым лучшим (берем полностью вектора юзера и пользователя и не применяем никаких обработок)

In [ ]:
#Печатные характеристики- улучшит ли добавление печатных характеристик качество 
#(используем подход, который дал наилучшее качество)- вариант 2

In [207]:
#обрабатываем бумагу
db['paper'] = ['пухофет' if 'пухлая офсетная' in x else x for x in db['paper']]
db['paper'] = ['офсет' if 'офсетная' in x else x for x in db['paper']]
db['paper'] = ['Офсет' if 'офсет' in x else x for x in db['paper']]
db['paper'] = ['картон' if 'Картон' in x else x for x in db['paper']]
db['paper'] = ['картон' if 'картон' in x else x for x in db['paper']]
db['paper'] = ['мелованная матовая' if 'мелованная матовая' in x else x for x in db['paper']]
db['paper'] = ['мелованный картон' if 'мелованный картон' in x else x for x in db['paper']]
db['paper'] = ['мелованная с ламинацией' if 'Мелованная с ламинацией' in x else x for x in db['paper']]
db['paper'] = ['писчая' if 'писчая' in x else x for x in db['paper']]
db['paper'] = ['классик' if 'Классик' in x else x for x in db['paper']]
db['paper'] = ['ЛюксКрим' if 'Lux Cream' in x else x for x in db['paper']]
db['paper'] = ['люкскрим' if 'ЛюксКрим' in x else x for x in db['paper']]
db['paper'] = ['ханартбулк' if 'ХанноАрт Булк' in x else x for x in db['paper']]
db['paper'] = ['камапух' if 'Кама' in x else x for x in db['paper']]
db['paper'] = ['ханноарт' if 'ХанноАрт' in x else x for x in db['paper']]
db['paper'] = ['ханноарт' if 'Ханноарт' in x else x for x in db['paper']]
db['paper'] = ['газетная' if 'газетная' in x else x for x in db['paper']]

In [208]:
tab_forX_books['paper'] = ['пухофет' if 'пухлая офсетная' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['офсет' if 'офсетная' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['офсет' if 'Офсет' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['картон' if 'Картон' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['картон' if 'картон' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['мелованная матовая' if 'мелованная матовая' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['мелованный картон' if 'мелованный картон' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['мелованная с ламинацией' if 'Мелованная с ламинацией' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['писчая' if 'писчая' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['классик' if 'Классик' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['ЛюксКрим' if 'Lux Cream' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['люкскрим' if 'ЛюксКрим' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['ханартбулк' if 'ХанноАрт Булк' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['камапух' if 'Кама' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['ханноарт' if 'ХанноАрт' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['ханноарт' if 'Ханноарт' in x else x for x in tab_forX_books['paper']]
tab_forX_books['paper'] = ['газетная' if 'газетная' in x else x for x in tab_forX_books['paper']]

In [209]:
#Обрабатываем cover
db['cover'] = [x.replace(' ', '') for x in db['cover']]

In [210]:
tab_forX_books['cover'] = [x.replace(' ', '') for x in tab_forX_books['cover']]

In [211]:
#Столбец качественных характеристик
db['qual_print'] = db['paper'] + ' ' + db['color'] + ' ' + db['cover']

In [212]:
tab_forX_books['qual_print'] = tab_forX_books['paper'] + ' ' + tab_forX_books['color'] + ' ' + tab_forX_books['cover']

In [213]:
#Вес
list_weight_seg = []
for i in db['nweight']:
    if i<=0.1:
        list_weight_seg.append('01')
    if i>0.1 and i<=0.15:
        list_weight_seg.append('01015')
    if i>0.15 and i<=0.2:
        list_weight_seg.append('01502')
    if i>0.2 and i<=0.25:
        list_weight_seg.append('02025')
    if i>0.25 and i<=0.3:
        list_weight_seg.append('02503')
    if i>0.3 and i<=0.4:
        list_weight_seg.append('030.4')
    if i>0.4 and i<=0.5:
        list_weight_seg.append('0405')
    if i>0.5 and i<=0.7:
        list_weight_seg.append('0507')
    if i>0.7 and i<=0.9:
        list_weight_seg.append('0709')
    if i>0.9:
        list_weight_seg.append('09')
db['nweight'] = list_weight_seg

In [214]:
list_weight_seg = []
for i in tab_forX_books['nweight']:
    if i<=0.1:
        list_weight_seg.append('01')
    if i>0.1 and i<=0.15:
        list_weight_seg.append('01015')
    if i>0.15 and i<=0.2:
        list_weight_seg.append('01502')
    if i>0.2 and i<=0.25:
        list_weight_seg.append('02025')
    if i>0.25 and i<=0.3:
        list_weight_seg.append('02503')
    if i>0.3 and i<=0.4:
        list_weight_seg.append('0304')
    if i>0.4 and i<=0.5:
        list_weight_seg.append('0405')
    if i>0.5 and i<=0.7:
        list_weight_seg.append('0507')
    if i>0.7 and i<=0.9:
        list_weight_seg.append('0709')
    if i>0.9:
        list_weight_seg.append('09')
tab_forX_books['nweight'] = list_weight_seg

In [215]:
#Pages
list_pages_seg = []
for i in db['pages']:
    if i<=10:
        list_pages_seg.append('10')
    if i>10 and i<=25:
        list_pages_seg.append('1025')
    if i>25 and i<=50:
        list_pages_seg.append('2550')
    if i>50 and i<=75:
        list_pages_seg.append('5075')
    if i>75 and i<=100:
        list_pages_seg.append('75100')
    if i>100 and i<=133:
        list_pages_seg.append('100133')
    if i>133 and i<=166:
        list_pages_seg.append('133166')
    if i>166 and i<=200:
        list_pages_seg.append('166200')
    if i>200 and i<=250:
        list_pages_seg.append('200250')    
    if i>250 and i<=300:
        list_pages_seg.append('250300')
    if i>300:
        list_pages_seg.append('300')
db['pages'] = list_pages_seg

In [216]:
list_pages_seg = []
for i in tab_forX_books['pages']:
    if i<=10:
        list_pages_seg.append('10')
    if i>10 and i<=25:
        list_pages_seg.append('1025')
    if i>25 and i<=50:
        list_pages_seg.append('2550')
    if i>50 and i<=75:
        list_pages_seg.append('5075')
    if i>75 and i<=100:
        list_pages_seg.append('75100')
    if i>100 and i<=133:
        list_pages_seg.append('100133')
    if i>133 and i<=166:
        list_pages_seg.append('133166')
    if i>166 and i<=200:
        list_pages_seg.append('166200')
    if i>200 and i<=250:
        list_pages_seg.append('200250')    
    if i>250 and i<=300:
        list_pages_seg.append('250300')
    if i>300:
        list_pages_seg.append('300')
tab_forX_books['pages'] = list_pages_seg

In [217]:
#Size
db['size1'] = [int(x[:x.find('*')]) for x in db['size']]
list_size1 = []
for i in db['size1']:
    if i<=180:
        list_size1.append('180')
    if i>180 and i<=220:
        list_size1.append('220')
    if i>220 and i<=260:
        list_size1.append('260')
    if i>260 and i<=300:
        list_size1.append('300')
    if i>300:
        list_size1.append('301')
db['size1'] = list_size1
db['size2'] = [int(x[(x.rfind('*')+1):]) for x in db['size']]
list_size2 = []
for i in db['size2']:
    if i<=8:
        list_size2.append('8')
    if i>8 and i<=10:
        list_size2.append('10')
    if i>10 and i<=18:
        list_size2.append('18')
    if i>18 and i<=80:
        list_size2.append('80')
    if i>80:
        list_size2.append('81')
db['size2'] = list_size2
db['size3'] = [int(x[(x.find('*')+1):x.rfind('*')]) for x in db['size']]
list_size3 = []
for i in db['size3']:
    if i<=160:
        list_size3.append('160')
    if i>160 and i<=210:
        list_size3.append('210')
    if i>210 and i<=220:
        list_size3.append('220')
    if i>220:
        list_size3.append('221')
db['size3'] = list_size3
db['size'] = db['size1'] + db['size2'] + db['size3']

In [218]:
tab_forX_books['size1'] = [int(x[:x.find('*')]) for x in tab_forX_books['size']]
list_size1 = []
for i in tab_forX_books['size1']:
    if i<=180:
        list_size1.append('180')
    if i>180 and i<=220:
        list_size1.append('220')
    if i>220 and i<=260:
        list_size1.append('260')
    if i>260 and i<=300:
        list_size1.append('300')
    if i>300:
        list_size1.append('301')
tab_forX_books['size1'] = list_size1
tab_forX_books['size2'] = [int(x[(x.rfind('*')+1):]) for x in tab_forX_books['size']]
list_size2 = []
for i in tab_forX_books['size2']:
    if i<=8:
        list_size2.append('8')
    if i>8 and i<=10:
        list_size2.append('10')
    if i>10 and i<=18:
        list_size2.append('18')
    if i>18 and i<=80:
        list_size2.append('80')
    if i>80:
        list_size2.append('81')
tab_forX_books['size2'] = list_size2
tab_forX_books['size3'] = [int(x[(x.find('*')+1):x.rfind('*')]) for x in tab_forX_books['size']]
list_size3 = []
for i in tab_forX_books['size3']:
    if i<=160:
        list_size3.append('160')
    if i>160 and i<=210:
        list_size3.append('210')
    if i>210 and i<=220:
        list_size3.append('220')
    if i>220:
        list_size3.append('221')
tab_forX_books['size3'] = list_size3
tab_forX_books['size'] = tab_forX_books['size1'] + tab_forX_books['size2'] + tab_forX_books['size3']

In [219]:
db['quan_print'] = db['nweight'] + ' ' + db['pages'] + ' ' + db['size']

In [220]:
tab_forX_books['quan_print'] = tab_forX_books['nweight'] + ' ' + tab_forX_books['pages'] + ' ' + tab_forX_books['size']

In [221]:
db['print'] = db['quan_print'] + ' ' + db['qual_print']

In [222]:
tab_forX_books['print'] = tab_forX_books['quan_print'] + ' ' + tab_forX_books['qual_print']

In [223]:
tab_print_usersForX = tabprep(tab_factor, 'print', 'OrderCustomerID')

100%|████████████████████████████████████████████████████████████████████████████| 16895/16895 [10:19<00:00, 27.25it/s]


In [224]:
tab_print_usersForX = tab_print_usersForX[['OrderCustomerID','print']]

In [227]:
tab_print_usersForX.drop_duplicates(inplace=True)
tab_print_usersForX.reset_index(inplace=True)
tab_print_usersForX.drop('index', axis=1, inplace=True)

In [228]:
vectorizer_print = TfidfVectorizer(ngram_range=(1,1))
tfidf_print = vectorizer_print.fit_transform(tab_print_usersForX['print'])

In [229]:
tab_print_usersForX['print'] = [x.split(' ') for x  in tab_print_usersForX['print']]

In [230]:
model1 = Word2Vec(min_count = 1,
                     window = 5,
                     size = 50,
                     sample = 6e-5, 
                     alpha = 0.03, 
                     min_alpha = 0.0007, 
                     workers = cores-1)

WARNING - 16:26:40: consider setting layer size to a multiple of 4 for greater performance
C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\gensim\models\base_any2vec.py:743: UserWarning: C extension not loaded, training will be slow. Install a C compiler and reinstall gensim for fast training.
  "C extension not loaded, training will be slow. "


In [231]:
%%time
model1.build_vocab(sentences = tab_print_usersForX['print'].values.tolist(), 
                  progress_per = 10000)

model1.train(sentences = tab_print_usersForX['print'].values.tolist(),
            total_examples = 1000, 
            epochs = 10, 
            report_delay = 1)

INFO - 16:26:42: collecting all words and their counts
INFO - 16:26:42: PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
INFO - 16:26:42: collected 134 word types from a corpus of 890885 raw words and 7835 sentences
INFO - 16:26:42: Loading a fresh vocabulary
INFO - 16:26:42: effective_min_count=1 retains 134 unique words (100% of original 134, drops 0)
INFO - 16:26:42: effective_min_count=1 leaves 890885 word corpus (100% of original 890885, drops 0)
INFO - 16:26:42: deleting the raw counts dictionary of 134 items
INFO - 16:26:42: sample=6e-05 downsamples 116 most-common words
INFO - 16:26:42: downsampling leaves estimated 62165 word corpus (7.0% of prior 890885)
INFO - 16:26:42: estimated required memory for 134 words and 50 dimensions: 120600 bytes
INFO - 16:26:42: resetting layer weights
INFO - 16:26:42: training model with 3 workers on 134 vocabulary and 50 features, using sg=0 hs=0 sample=6e-05 negative=5 window=5
INFO - 16:26:43: EPOCH 1 - PROGRESS: at 8.20% exa

WARNING - 16:28:06: EPOCH - 3 : supplied example count (7835) did not equal expected count (1000)
INFO - 16:28:08: EPOCH 4 - PROGRESS: at 41.30% examples, 1536 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:10: EPOCH 4 - PROGRESS: at 97.00% examples, 1873 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:11: EPOCH 4 - PROGRESS: at 125.90% examples, 2049 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:12: EPOCH 4 - PROGRESS: at 163.70% examples, 2125 words/s, in_qsize 6, out_qsize 0
INFO - 16:28:13: EPOCH 4 - PROGRESS: at 193.00% examples, 2109 words/s, in_qsize 6, out_qsize 0
INFO - 16:28:15: EPOCH 4 - PROGRESS: at 229.70% examples, 2101 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:16: EPOCH 4 - PROGRESS: at 267.10% examples, 2119 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:17: EPOCH 4 - PROGRESS: at 297.90% examples, 2143 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:18: EPOCH 4 - PROGRESS: at 325.60% examples, 2132 words/s, in_qsize 5, out_qsize 0
INFO - 16:28:19: EPOCH 4 - PROGRESS: at 

INFO - 16:29:40: EPOCH 7 - PROGRESS: at 325.60% examples, 2228 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:42: EPOCH 7 - PROGRESS: at 358.60% examples, 2127 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:43: EPOCH 7 - PROGRESS: at 388.10% examples, 2227 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:44: EPOCH 7 - PROGRESS: at 415.40% examples, 2218 words/s, in_qsize 6, out_qsize 0
INFO - 16:29:45: EPOCH 7 - PROGRESS: at 446.50% examples, 2214 words/s, in_qsize 6, out_qsize 0
INFO - 16:29:47: EPOCH 7 - PROGRESS: at 484.90% examples, 2178 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:48: EPOCH 7 - PROGRESS: at 504.00% examples, 2184 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:49: EPOCH 7 - PROGRESS: at 540.70% examples, 2195 words/s, in_qsize 6, out_qsize 0
INFO - 16:29:51: EPOCH 7 - PROGRESS: at 570.90% examples, 2180 words/s, in_qsize 6, out_qsize 0
INFO - 16:29:52: EPOCH 7 - PROGRESS: at 615.10% examples, 2192 words/s, in_qsize 5, out_qsize 0
INFO - 16:29:53: EPOCH 7 - PROGRESS: at 

INFO - 16:31:15: EPOCH 10 - PROGRESS: at 615.10% examples, 2217 words/s, in_qsize 5, out_qsize 0
INFO - 16:31:16: EPOCH 10 - PROGRESS: at 658.70% examples, 2226 words/s, in_qsize 5, out_qsize 0
INFO - 16:31:17: EPOCH 10 - PROGRESS: at 718.60% examples, 2224 words/s, in_qsize 5, out_qsize 0
INFO - 16:31:18: EPOCH 10 - PROGRESS: at 746.00% examples, 2233 words/s, in_qsize 6, out_qsize 0
INFO - 16:31:19: EPOCH 10 - PROGRESS: at 758.70% examples, 2233 words/s, in_qsize 5, out_qsize 0
INFO - 16:31:20: EPOCH 10 - PROGRESS: at 777.40% examples, 2225 words/s, in_qsize 2, out_qsize 1
INFO - 16:31:20: worker thread finished; awaiting finish of 2 more threads
INFO - 16:31:20: worker thread finished; awaiting finish of 1 more threads
INFO - 16:31:20: worker thread finished; awaiting finish of 0 more threads
INFO - 16:31:20: EPOCH - 10 : training on 890885 raw words (62381 effective words) took 27.7s, 2253 effective words/s
WARNING - 16:31:20: EPOCH - 10 : supplied example count (7835) did not equa

Wall time: 4min 38s


In [232]:
#Формируем матрицу печатный фактор-вектор
print_matrix = []
for j in tqdm(range(len(vectorizer_print.get_feature_names()))):
    try:
        res = model1[vectorizer_print.get_feature_names()[j]]
    except:
        res = np.zeros(50)
    print_matrix.append(res)

  0%|                                                                                          | 0/126 [00:00<?, ?it/s]C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:5: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  """
100%|██████████████████████████████████████████████████████████████████████████████| 126/126 [00:00<00:00, 4029.72it/s]


In [233]:
print_matrix

[array([ 0.01343559, -1.146859  , -0.50895137, -0.3675957 ,  0.39884302,
         0.24569562, -0.47851136,  0.6355011 , -1.0430629 , -0.30047387,
         0.1283851 ,  0.43047357, -0.16223589,  0.87644756, -0.7658217 ,
        -0.3265468 ,  0.10125761,  0.20266873,  0.283324  ,  0.351935  ,
        -0.7770044 , -0.05757085,  0.082008  ,  0.56451076,  0.8490858 ,
         0.14689071,  0.29659978, -0.6613863 ,  0.39018744, -1.2290398 ,
         1.1287489 , -0.4139826 ,  0.6679139 ,  0.23807715,  0.21617885,
         0.1798916 , -0.08663368,  0.193769  ,  0.6173255 ,  1.0849444 ,
         0.589714  , -0.49283108, -0.31075186, -0.78821236,  1.0559931 ,
        -1.0554255 , -0.5277865 ,  0.29181388,  0.43821755,  0.14054658],
       dtype=float32),
 array([ 0.5217522 , -0.8426242 , -0.7208666 ,  0.09088995,  0.49259433,
         0.5111131 , -0.28765786,  0.28348285, -0.97992176,  0.34221756,
         0.5719282 ,  0.83649117,  0.10203687,  0.6875516 , -0.5984856 ,
        -0.39975873, -0.183

In [234]:
count_print_user = np.dot(tfidf_print.toarray(),np.array(print_matrix))

In [235]:
count_print_user = [list(x) for x in count_print_user]

In [236]:
tab_print_usersForX['count_print_user'] = count_print_user

In [237]:
tfidf_print_books = vectorizer_print.transform(tab_forX_books['print'])

In [238]:
tab_forX_books['print'] = [x.split(' ') for x  in tab_forX_books['print']]

In [239]:
count_print_books = np.dot(tfidf_print_books.toarray(),np.array(print_matrix))

In [240]:
count_print_books = [list(x) for x in count_print_books]

In [241]:
tab_forX_books['count_print_books'] = count_print_books

In [242]:
tab_forX_books = tab_forX_books.merge(tab_print_usersForX[['OrderCustomerID', 'count_print_user']], 
                                    how = 'left', 
                                    on = 'OrderCustomerID')

In [243]:
#tab_forX_books.drop('count_print_user', axis=1, inplace=True)

In [244]:
tab_forX_books['count_print_user'][5]

[0.10014370860785593,
 -1.0496895967033042,
 0.925814603923439,
 0.9249225215127297,
 1.4248940062820552,
 0.5334253278816002,
 -0.9091165045983228,
 0.055580903938951064,
 -0.9404031331614376,
 -0.24967249402212732,
 0.5872479062043816,
 0.7610168666670817,
 -1.504454072610976,
 -0.3411127828114969,
 -0.5169038119199979,
 -1.607775820171547,
 0.3205039338809467,
 -0.5402413971417839,
 1.2846355927863555,
 -0.253514321141785,
 0.6060775341572757,
 1.1016450830223388,
 -0.6441191936221748,
 1.4058170591985522,
 0.998185347558539,
 -0.8283087105653666,
 0.8285253970978109,
 0.1576047110843089,
 0.6117658862339117,
 -0.1703325939273,
 0.09531547467104773,
 -0.7998071818092671,
 1.8516877877187212,
 -0.315030623219116,
 -0.2904521890236552,
 0.9476657163940237,
 0.6523205563881153,
 -1.7497085396312997,
 0.33873034082746545,
 1.8780507474422103,
 1.3962338004952073,
 0.11672058622928468,
 0.0547417091120206,
 -1.4642639206106758,
 0.43087071828898205,
 -1.0957784319160428,
 -0.483666316263

In [245]:
X_train_print, X_test_print, y_train_print, y_test_print = train_test_split(tab_forX_books, target, 
                                                                           test_size = 0.6, 
                                                                           random_state = 42)

In [ ]:
#Вариант 1 с print factor-косинусное расстояние

In [246]:
factor_print = []
for i in tqdm(range(len(X_test_print))):
    factor_print.append(cosine(X_test_print['count_print_books'].values.tolist()[i],
                               X_test_print['count_print_user'].values.tolist()[i]))

100%|███████████████████████████████████████████████████████████████████████████| 89187/89187 [08:13<00:00, 180.86it/s]


In [247]:
X = pd.concat([theme_factor, age_features, pd.DataFrame(factor_tag), pd.DataFrame(factor_print)], axis = 1, ignore_index = True)

In [248]:
X_train_pr, X_test_pr, y_train_pr, y_test_pr = train_test_split(X, y_test_tag, test_size=0.2, random_state=42)

In [249]:
data = X_train_pr
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


Accuracy составляет 0.9306
Precision составляет 0.9200


In [250]:
y_pred = bst.predict(dtest)
for_test = test_recommendations(y_pred)

In [251]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:29<00:00, 23.77it/s]


In [252]:
metric[0]

0.3693387423603621

In [ ]:
#Mean average precision at k для варианта 1 с print factor составляет 37%

In [ ]:
#Лучше не стало

In [ ]:
#Варитант 2 с print factor. Берем не косинусное расстояние, а вектора полностью

In [255]:
factor_print = [list(X_test_print['count_print_books'].values.tolist()[i]) + list(X_test_print['count_print_user'].values.tolist()[i]) for i in range(len(X_test_print))]

In [256]:
X = pd.concat([theme_factor, age_features, pd.DataFrame(factor_tag), pd.DataFrame(factor_print)], axis=1, ignore_index=True)

In [257]:
X_train_pr, X_test_pr, y_train_pr, y_test_pr = train_test_split(X, y_test_tag, test_size=0.2, random_state=42)

In [258]:
data = X_train_pr
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

C:\Users\n.volkova\AppData\Local\Continuum\anaconda3\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


Accuracy составляет 0.9357
Precision составляет 0.9242


In [259]:
for_test = test_recommendations(y_pred)

In [260]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:17<00:00, 24.64it/s]


In [261]:
metric[0]

0.3682241314507958

In [ ]:
#Mean average precision at k для варианта 2 c print factor составляет 37%

In [ ]:
#Mean average precision at k с добавлением печатных характеристик не стало лучше
#Но немного стало лучше precision и accuracy
#Проблема в том, что выбранный способ использования - по каждой книге отобрать людей, которые максимально вероятно
#ее купят, и чем больше будет людей, тем лучше- поэтому precision и accuracy импеют значение
#Поэтому на данное время оставляем вариант 2 с печатными характеристиками

In [ ]:
#Отсев фич

In [ ]:
#Используем рандомный лес и permutation importance для отсева фич

In [ ]:
#Обучим рандомный лес

In [328]:
r_forest_for_features = RandomForestClassifier(n_estimators=100, random_state=0)
r_forest_for_features.fit(X_train_pr, y_train_pr)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=None,
            oob_score=False, random_state=0, verbose=0, warm_start=False)

In [330]:
X_test_pr1, X_test_pr2, y_test_pr1, y_test_pr2 = train_test_split(X_test_pr, y_test_pr, test_size=0.5, random_state=42)

In [ ]:
#permutation importance

In [331]:
import eli5
from eli5.sklearn import PermutationImportance

perm = PermutationImportance(r_forest_for_features, random_state=1).fit(X_test_pr1, y_test_pr1)

In [332]:
eli5.show_weights(perm, feature_names = [str(x) for x in X_train_pr.columns.tolist()])

In [ ]:
#ранг по permutation importance

In [362]:
feature_table_per = pd.concat([pd.DataFrame(perm.feature_importances_),
                             pd.DataFrame(X_train_pr.columns.tolist())],axis=1)

In [363]:
feature_table_per.columns = ['feature_importance_per','feature_name_per']

In [365]:
feature_table_per=feature_table_per.sort_values(by='feature_importance_per', ascending=False)

In [366]:
feature_table_per['rank_per'] = range(315)

In [ ]:
#ранг по важности факторов по случайному лесу

In [367]:
feature_table_for = pd.concat([pd.DataFrame(r_forest_for_features.feature_importances_),
                             pd.DataFrame(X_train_pr.columns.tolist())],axis=1)

In [368]:
feature_table_for.columns = ['feature_importance_for','feature_name_for']

In [369]:
feature_table_for = feature_table_for.sort_values(by='feature_importance_for', ascending=False)

In [370]:
feature_table_for['rank_for'] = range(315)

In [371]:
feature_table_for.head()

feature_importance_for  feature_name_for  rank_for
92                0.035871                92         0
82                0.022280                82         1
81                0.019435                81         2
68                0.018647                68         3
25                0.018027                25         4

In [ ]:
#Объединяем таблицы

In [372]:
feature_table_per = feature_table_per.sort_values(by='feature_name_per')
feature_table_for = feature_table_for.sort_values(by='feature_name_for')

In [373]:
feature_table_per.reset_index(inplace=True)
feature_table_per.drop('index', axis=1, inplace=True)

In [374]:
feature_table_for.reset_index(inplace=True)
feature_table_for.drop('index', axis=1, inplace=True)

In [375]:
feature_tab=pd.concat([feature_table_per, feature_table_for], axis=1)

In [ ]:
#Считаем совокупный ранг

In [377]:
feature_tab['total_importance'] = feature_tab['rank_per']*feature_tab['rank_for']

In [378]:
feature_tab=feature_tab.sort_values(by = 'total_importance')

In [382]:
feature_tab.head()

feature_importance_per  feature_name_per  rank_per  \
92                0.002310                92         0   
82                0.000785                82         9   
68                0.000875                68         5   
81                0.000785                81        10   
43                0.001144                43         2   

    feature_importance_for  feature_name_for  rank_for  total_importance  
92                0.035871                92         0                 0  
82                0.022280                82         1                 9  
68                0.018647                68         3                15  
81                0.019435                81         2                20  
43                0.008812                43        20                40

In [394]:
feature_tab[feature_tab['feature_importance_per']<0].shape

(131, 7)

In [ ]:
#треть факторов можно убрать, поэтому убираем 100 наихудших факторов по совокупному рейтингу

In [391]:
features_totake = feature_tab['feature_name_for'].values.tolist()[:-100]

In [392]:
data = X_train_pr[features_totake]
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param = {'max_depth': 12}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr[features_totake]
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

Accuracy составляет 0.9368
Precision составляет 0.9261


In [ ]:
#Метрики выросли

In [395]:
for_test = test_recommendations(y_pred)

In [396]:
metric = mean_av_precision_at_k(for_test, 10)

100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:18<00:00, 24.63it/s]


In [397]:
metric[0]

0.3622028984323081

In [ ]:
#Релевантность упала, но в контексте использования рекомендаций нас это волнует меньше, 
#в случае изменения контекста на это нужно обратить внимание

In [ ]:
#Оптимазация xgboost

In [417]:
data = X_train_pr[features_totake]
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
model_select={}
for depth in tqdm([5,10,12,15]):
    for sample in tqdm([0.06, 0.5, 0.7, 1]):
        for alpha in tqdm([0, 0.001,  0.01]):
            for lambda_1 in [1,1.1]:
                param = {'max_depth': depth, 'subsample':sample, 'colsample_bytree':sample, 'alpha':alpha, 'lambda':lambda_1 }
                cv_result = xgb.cv(param, dtrain, 
                           num_boost_round=100, nfold=5, 
                           stratified=False, folds=None, metrics='error', obj=None, 
                           feval=None, maximize=False, early_stopping_rounds=None, fpreproc=None, 
                           verbose_eval=None, show_stdv=True, seed=0, callbacks=None, shuffle=True)
                name = str(depth)+','+str(sample)+','+str(alpha)+','+str(lambda_1)
                model_select[name] = cv_result     




  0%|                                                                                            | 0/4 [00:00<?, ?it/s]



  0%|                                                                                            | 0/4 [00:00<?, ?it/s]




  0%|                                                                                            | 0/3 [00:00<?, ?it/s]




 33%|████████████████████████████                                                        | 1/3 [01:02<02:05, 62.53s/it]




 67%|████████████████████████████████████████████████████████                            | 2/3 [02:03<01:02, 62.13s/it]




100%|████████████████████████████████████████████████████████████████████████████████████| 3/3 [03:08<00:00, 62.78s/it]



 25%|████████████████████▊                                                              | 1/4 [03:08<09:24, 188.02s/it]




  0%|                                                                                            | 0/3 [00:00<?, ?it/s]




 33%|██

 75%|████████████████████████████████████████████████████████████                    | 3/4 [2:29:35<45:38, 2738.53s/it]



  0%|                                                                                            | 0/4 [00:00<?, ?it/s]




  0%|                                                                                            | 0/3 [00:00<?, ?it/s]




 33%|████████████████████████████                                                        | 1/3 [01:28<02:56, 88.36s/it]




 67%|████████████████████████████████████████████████████████                            | 2/3 [02:56<01:28, 88.34s/it]




100%|████████████████████████████████████████████████████████████████████████████████████| 3/3 [04:24<00:00, 88.19s/it]



 25%|████████████████████▊                                                              | 1/4 [04:24<13:13, 264.50s/it]




  0%|                                                                                            | 0/3 [00:00<?, ?it/s]




 33%|█████

In [423]:
model_best = {}
for i in model_select.keys():
    model_best[i] = model_select[i]['test-error-mean'][99]

In [ ]:
#Вычленяем из списка оптимальные параметры

In [430]:
list(model_best.values()).index(min(model_best.values()))

46

In [432]:
list(model_select.keys())[46]

'10,1,0.01,1'

In [ ]:
#Обучаем с оптимальными параметрами

In [433]:
data = X_train_pr[features_totake]
label = y_train_pr
dtrain = xgb.DMatrix(data, label=label)
param =  {'max_depth': 10, 'subsample': 1, 'colsample_bytree': 1, 'alpha': 0.01, 'lambda': 1}
num_round = 100
bst = xgb.train(param, dtrain, num_round)
data_test = X_test_pr[features_totake]
dtest = xgb.DMatrix(data_test)
y_pred = bst.predict(dtest)
y_pred1=[1 if x>0.5 else 0 for x in y_pred]
print('Accuracy составляет {0:.4f}'.format(accuracy_score(y_pred1, y_test_pr.values.tolist())))
print('Precision составляет {0:.4f}'.format(precision_score(y_pred1, y_test_pr.values.tolist())))

Accuracy составляет 0.9373
Precision составляет 0.9265


In [434]:
for_test = test_recommendations(y_pred)

In [435]:
metric = mean_av_precision_at_k(for_test, 10)




  0%|                                                                                         | 0/7835 [00:00<?, ?it/s]


  0%|                                                                                 | 1/7835 [00:00<26:49,  4.87it/s]


  0%|                                                                                 | 2/7835 [00:00<23:20,  5.59it/s]


  0%|                                                                                 | 4/7835 [00:00<18:55,  6.90it/s]


  0%|                                                                                 | 6/7835 [00:00<15:20,  8.50it/s]


  0%|                                                                                 | 8/7835 [00:00<12:42, 10.26it/s]


  0%|                                                                                | 10/7835 [00:00<11:13, 11.63it/s]


  0%|▏                                                                               | 13/7835 [00:00<09:46, 13.34it/s]


  0%|▏               

  2%|█▉                                                                             | 187/7835 [00:08<05:25, 23.50it/s]


  2%|█▉                                                                             | 190/7835 [00:09<05:25, 23.50it/s]


  2%|█▉                                                                             | 193/7835 [00:09<05:23, 23.61it/s]


  3%|█▉                                                                             | 196/7835 [00:09<05:21, 23.73it/s]


  3%|██                                                                             | 199/7835 [00:09<05:19, 23.89it/s]


  3%|██                                                                             | 202/7835 [00:09<05:18, 24.00it/s]


  3%|██                                                                             | 205/7835 [00:09<05:15, 24.18it/s]


  3%|██                                                                             | 208/7835 [00:09<05:15, 24.14it/s]


  3%|██▏                

  5%|███▉                                                                           | 388/7835 [00:17<05:06, 24.26it/s]


  5%|███▉                                                                           | 391/7835 [00:17<05:09, 24.08it/s]


  5%|███▉                                                                           | 394/7835 [00:17<05:08, 24.13it/s]


  5%|████                                                                           | 397/7835 [00:17<05:06, 24.23it/s]


  5%|████                                                                           | 400/7835 [00:17<05:06, 24.24it/s]


  5%|████                                                                           | 403/7835 [00:17<05:05, 24.30it/s]


  5%|████                                                                           | 406/7835 [00:18<05:05, 24.29it/s]


  5%|████                                                                           | 409/7835 [00:18<05:05, 24.28it/s]


  5%|████▏              

  8%|█████▉                                                                         | 589/7835 [00:25<04:58, 24.30it/s]


  8%|█████▉                                                                         | 592/7835 [00:25<04:59, 24.17it/s]


  8%|█████▉                                                                         | 595/7835 [00:25<04:59, 24.14it/s]


  8%|██████                                                                         | 598/7835 [00:26<04:58, 24.24it/s]


  8%|██████                                                                         | 601/7835 [00:26<04:58, 24.24it/s]


  8%|██████                                                                         | 604/7835 [00:26<04:58, 24.25it/s]


  8%|██████                                                                         | 607/7835 [00:26<04:58, 24.25it/s]


  8%|██████▏                                                                        | 610/7835 [00:26<04:58, 24.20it/s]


  8%|██████▏            

 10%|███████▉                                                                       | 790/7835 [00:34<04:52, 24.11it/s]


 10%|███████▉                                                                       | 793/7835 [00:34<04:50, 24.22it/s]


 10%|████████                                                                       | 796/7835 [00:34<04:52, 24.05it/s]


 10%|████████                                                                       | 799/7835 [00:34<04:53, 24.00it/s]


 10%|████████                                                                       | 802/7835 [00:34<04:53, 23.96it/s]


 10%|████████                                                                       | 805/7835 [00:34<04:52, 24.05it/s]


 10%|████████▏                                                                      | 808/7835 [00:34<04:51, 24.11it/s]


 10%|████████▏                                                                      | 811/7835 [00:34<04:51, 24.10it/s]


 10%|████████▏          

...

 90%|█████████████████████████████████████████████████████████████████████▊        | 7016/7835 [04:56<00:33, 24.36it/s]


 90%|█████████████████████████████████████████████████████████████████████▉        | 7019/7835 [04:56<00:33, 24.39it/s]


 90%|█████████████████████████████████████████████████████████████████████▉        | 7022/7835 [04:56<00:33, 24.28it/s]


 90%|█████████████████████████████████████████████████████████████████████▉        | 7025/7835 [04:56<00:33, 24.33it/s]


 90%|█████████████████████████████████████████████████████████████████████▉        | 7028/7835 [04:56<00:33, 24.31it/s]


 90%|█████████████████████████████████████████████████████████████████████▉        | 7031/7835 [04:56<00:33, 23.94it/s]


 90%|██████████████████████████████████████████████████████████████████████        | 7034/7835 [04:57<00:33, 23.92it/s]


 90%|██████████████████████████████████████████████████████████████████████        | 7037/7835 [04:57<00:33, 24.14it/s]


 90%|███████████████████

 92%|███████████████████████████████████████████████████████████████████████▊      | 7217/7835 [05:04<00:25, 24.14it/s]


 92%|███████████████████████████████████████████████████████████████████████▉      | 7220/7835 [05:04<00:25, 24.24it/s]


 92%|███████████████████████████████████████████████████████████████████████▉      | 7223/7835 [05:04<00:25, 23.95it/s]


 92%|███████████████████████████████████████████████████████████████████████▉      | 7226/7835 [05:04<00:25, 24.16it/s]


 92%|███████████████████████████████████████████████████████████████████████▉      | 7229/7835 [05:05<00:25, 24.19it/s]


 92%|███████████████████████████████████████████████████████████████████████▉      | 7232/7835 [05:05<00:25, 23.98it/s]


 92%|████████████████████████████████████████████████████████████████████████      | 7235/7835 [05:05<00:24, 24.00it/s]


 92%|████████████████████████████████████████████████████████████████████████      | 7238/7835 [05:05<00:24, 24.02it/s]


 92%|███████████████████

 95%|█████████████████████████████████████████████████████████████████████████▊    | 7418/7835 [05:12<00:17, 24.06it/s]


 95%|█████████████████████████████████████████████████████████████████████████▉    | 7421/7835 [05:13<00:17, 24.24it/s]


 95%|█████████████████████████████████████████████████████████████████████████▉    | 7424/7835 [05:13<00:16, 24.30it/s]


 95%|█████████████████████████████████████████████████████████████████████████▉    | 7427/7835 [05:13<00:16, 24.23it/s]


 95%|█████████████████████████████████████████████████████████████████████████▉    | 7430/7835 [05:13<00:16, 24.07it/s]


 95%|█████████████████████████████████████████████████████████████████████████▉    | 7433/7835 [05:13<00:16, 24.02it/s]


 95%|██████████████████████████████████████████████████████████████████████████    | 7436/7835 [05:13<00:16, 24.09it/s]


 95%|██████████████████████████████████████████████████████████████████████████    | 7439/7835 [05:13<00:16, 24.14it/s]


 95%|███████████████████

 97%|███████████████████████████████████████████████████████████████████████████▊  | 7619/7835 [05:21<00:09, 23.16it/s]


 97%|███████████████████████████████████████████████████████████████████████████▉  | 7622/7835 [05:21<00:09, 23.43it/s]


 97%|███████████████████████████████████████████████████████████████████████████▉  | 7625/7835 [05:21<00:08, 23.39it/s]


 97%|███████████████████████████████████████████████████████████████████████████▉  | 7628/7835 [05:21<00:08, 23.65it/s]


 97%|███████████████████████████████████████████████████████████████████████████▉  | 7631/7835 [05:22<00:08, 23.60it/s]


 97%|███████████████████████████████████████████████████████████████████████████▉  | 7634/7835 [05:22<00:08, 23.52it/s]


 97%|████████████████████████████████████████████████████████████████████████████  | 7637/7835 [05:22<00:08, 23.73it/s]


 98%|████████████████████████████████████████████████████████████████████████████  | 7640/7835 [05:22<00:08, 23.83it/s]


 98%|███████████████████

100%|█████████████████████████████████████████████████████████████████████████████▊| 7820/7835 [05:30<00:00, 23.30it/s]


100%|█████████████████████████████████████████████████████████████████████████████▉| 7823/7835 [05:30<00:00, 23.25it/s]


100%|█████████████████████████████████████████████████████████████████████████████▉| 7826/7835 [05:30<00:00, 23.43it/s]


100%|█████████████████████████████████████████████████████████████████████████████▉| 7829/7835 [05:30<00:00, 23.56it/s]


100%|█████████████████████████████████████████████████████████████████████████████▉| 7832/7835 [05:30<00:00, 23.54it/s]


100%|██████████████████████████████████████████████████████████████████████████████| 7835/7835 [05:30<00:00, 23.64it/s]

In [436]:
metric[0]

0.36576525748711747

In [441]:
model_select['10,1,0.01,1'].iloc[99,:]

train-error-mean    0.000869
train-error-std     0.000355
test-error-mean     0.063140
test-error-std      0.000787
Name: 99, dtype: float64

In [ ]:
#Стандартное отклонение по валидации оптимально

In [ ]:
#Вывод: мы получили стабильную модель, которая показывает хорошие результаты для того способа модели, который был выбран.
#К определенной книге мы будем подтягивать всех пользователей, которые вероятно ее купят